<a href="https://colab.research.google.com/github/PedroGuimaraesFerreira/Py_Projects/blob/master/Covid_19_Capstone.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Novel Coronavirus (COVID-19)** - Creating insights from live data


##### Pedro Guimarães Ferreira



# A. **Introduction**
---

> On the 31st December 2019, China first reported to the World Health Organization (WHO) a pneumonia of unknown cause in the city of Wuhan. On the 22nd January 2020, WHO issued a statement showing that there was evidence of human-to-human transmission in the aforementioned city. On the 30th January 2020, the Emergency Committee (EC) reached consensus and advised WHO Director-General that the outbreak constituted a Public Health Emergency of International Concern (PHEIC)  and the novel coronavirus outbreak (2019-nCoV) was declared. On the 11th March 2020, with drastics concerns about the rapid spread and severity, WHO characterized COVID-19 as a pandemic [1].
 
> The World Health Organization (WHO) defines the Coronavirus Disease (COVID-19) as an infectious disease, which inflicts, on most of the affected, mild to moderate respiratory illness and recovery happens without requiring special treatment. However, people in advanced ages, with cardiovascular diseases, diabetes, chronic respiratory disease, and cancer are prone to experience substantially more severe illness [2]. Still according to WHO,  COVID-19's most common symptoms are fever, dry cough and tiredness and some of the most serious ones are difficulty breathing, chest, lost of speech or movement and might lead to death, if immediate medical attention is not seeked [3].
 
> Considering the aforementioned, this project aims at providing meaningful insights on the characteristics of the worldwide spread of COVID-19, by making use of clustering and visualization techniques. Namely, identifying within clusters geographical/demographic data patterns, as well as providing similarities within regions/income groups of countries. The insights obtained and patterns identified have as end goal supplying the world authorities and health professionals (stakeholders) some light when dealing with the overwhelming challenges that this pandemic scenario imposes upon society as a whole.


# B. **Data**
---

> In order to provide data driven answers, a  COVID-19 Github repository, made public by Johns Hopkins University's Center for Systems Science and Engineering (CSSEGISandData), was used as data source in this project [4]. The repository contains data, in time series format, regarding worldwide COVID-19 data, split into three categories: accumulated confirmed cases, accumulated deaths and accumulated recoveries, all three are updated on a daily basis. The last time this code was run before been submitted to Coursera was 5/23/20

> Additionally, with the objective of enriching subsequent data analysis, countries' data concerning economic and demographic characteristics was obtained in the The World Bank website [5]. The specifics of the mentioned data are better detailed along this section of the project.


### **B.1** Importing the necessary libraries




In [1]:
import matplotlib.pyplot as plt 
import matplotlib.cm as cm
import matplotlib.colors as mcolors
import seaborn as sns
import matplotlib.dates as mdates
!pip install plotly==4.5.2
import plotly.express as px
import plotly.offline as py

import numpy as np
import pandas as pd 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import pandas_profiling
from pandas_profiling import ProfileReport

from sklearn.cluster import KMeans
from sklearn.preprocessing import MinMaxScaler

/usr/local/lib/python3.6/dist-packages/statsmodels/tools/_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


     |████████████████████████████████| 7.1MB 3.8MB/s 
  Found existing installation: plotly 4.4.1
    Uninstalling plotly-4.4.1:
      Successfully uninstalled plotly-4.4.1


### **B.2** Importing raw COVID-19 data into three different data frames, as well as additional countries' data into two others


In [0]:
confirmed_df = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv')

deaths_df = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_global.csv')

recoveries_df = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_recovered_global.csv')

countries_df = pd.read_csv('https://raw.githubusercontent.com/PedroGuimaraesFerreira/Py_Projects/master/df_countries.csv')

alpha_2 = pd.read_csv('https://raw.githubusercontent.com/PedroGuimaraesFerreira/Py_Projects/master/alpha2.csv', sep=';')

> ### B.2.1 Checking the three data frames regarding COVID-19's data starting from 1/22/2020 (daily updated) and last uptaded 5/23/20 before being submited to Coursera


  *   confirmed_df : contains countries' time series data of the evolution of confirmed cases (cases values are accumulated as time increases in the time series); 

  *   deaths_df : contains countries' time series data of the evolution of deaths (deaths values are accumulated as time increases in time series); 

  *   recoveries_df : contains countries' time series data of the evolution of recovered cases (cases values are accumulated as time increases in time series); 






In [0]:
print('\n\n--- Acummulated Confirmed Cases Worlwide ---\n')
display(confirmed_df.head(10))
print('\n\n--- Acummulated Number of Deaths Wordlwide ---\n')
display(deaths_df.head(10))
print('\n\n--- Acummulated Number of Recovered Cases Worlwide ---\n')
display(recoveries_df.head(10))



--- Acummulated Confirmed Cases Worlwide ---



Province/State       Country/Region      Lat      Long  \
0                           NaN          Afghanistan  33.0000   65.0000   
1                           NaN              Albania  41.1533   20.1683   
2                           NaN              Algeria  28.0339    1.6596   
3                           NaN              Andorra  42.5063    1.5218   
4                           NaN               Angola -11.2027   17.8739   
5                           NaN  Antigua and Barbuda  17.0608  -61.7964   
6                           NaN            Argentina -38.4161  -63.6167   
7                           NaN              Armenia  40.0691   45.0382   
8  Australian Capital Territory            Australia -35.4735  149.0124   
9               New South Wales            Australia -33.8688  151.2093   

   1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  1/27/20  1/28/20  1/29/20  \
0        0        0        0        0        0        0        0        0   
1        0        0        0        0        0        0        0        0   
2        0        0        0        0        0        0        0        0   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   
5        0        0        0        0        0        0        0        0   
6        0        0        0        0        0        0        0        0   
7        0        0        0        0        0        0        0        0   
8        0        0        0        0        0        0        0        0   
9        0        0        0        0        3        4        4        4   

   1/30/20  1/31/20  2/1/20  2/2/20  2/3/20  2/4/20  2/5/20  2/6/20  2/7/20  \
0        0        0       0       0       0       0       0       0       0   
1        0        0       0       0       0       0       0       0       0   
2        0        0       0       0       0       0       0       0       0   
3        0        0       0       0       0       0       0       0       0   
4        0        0       0       0       0       0       0       0       0   
5        0        0       0       0       0       0       0       0       0   
6        0        0       0       0       0       0       0       0       0   
7        0        0       0       0       0       0       0       0       0   
8        0        0       0       0       0       0       0       0       0   
9        4        4       4       4       4       4       4       4       4   

   2/8/20  2/9/20  2/10/20  2/11/20  2/12/20  2/13/20  2/14/20  2/15/20  \
0       0       0        0        0        0        0        0        0   
1       0       0        0        0        0        0        0        0   
2       0       0        0        0        0        0        0        0   
3       0       0        0        0        0        0        0        0   
4       0       0        0        0        0        0        0        0   
5       0       0        0        0        0        0        0        0   
6       0       0        0        0        0        0        0        0   
7       0       0        0        0        0        0        0        0   
8       0       0        0        0        0        0        0        0   
9       4       4        4        4        4        4        4        4   

   2/16/20  2/17/20  2/18/20  2/19/20  2/20/20  2/21/20  2/22/20  2/23/20  \
0        0        0        0        0        0        0        0        0   
1        0        0        0        0        0        0        0        0   
2        0        0        0        0        0        0        0        0   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   
5        0        0        0        0        0        0        0        0   
6        0        0        0        0        0        0        0        0   
7        0        0        0   



--- Acummulated Number of Deaths Wordlwide ---



Province/State       Country/Region      Lat      Long  \
0                           NaN          Afghanistan  33.0000   65.0000   
1                           NaN              Albania  41.1533   20.1683   
2                           NaN              Algeria  28.0339    1.6596   
3                           NaN              Andorra  42.5063    1.5218   
4                           NaN               Angola -11.2027   17.8739   
5                           NaN  Antigua and Barbuda  17.0608  -61.7964   
6                           NaN            Argentina -38.4161  -63.6167   
7                           NaN              Armenia  40.0691   45.0382   
8  Australian Capital Territory            Australia -35.4735  149.0124   
9               New South Wales            Australia -33.8688  151.2093   

   1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  1/27/20  1/28/20  1/29/20  \
0        0        0        0        0        0        0        0        0   
1        0        0        0        0        0        0        0        0   
2        0        0        0        0        0        0        0        0   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   
5        0        0        0        0        0        0        0        0   
6        0        0        0        0        0        0        0        0   
7        0        0        0        0        0        0        0        0   
8        0        0        0        0        0        0        0        0   
9        0        0        0        0        0        0        0        0   

   1/30/20  1/31/20  2/1/20  2/2/20  2/3/20  2/4/20  2/5/20  2/6/20  2/7/20  \
0        0        0       0       0       0       0       0       0       0   
1        0        0       0       0       0       0       0       0       0   
2        0        0       0       0       0       0       0       0       0   
3        0        0       0       0       0       0       0       0       0   
4        0        0       0       0       0       0       0       0       0   
5        0        0       0       0       0       0       0       0       0   
6        0        0       0       0       0       0       0       0       0   
7        0        0       0       0       0       0       0       0       0   
8        0        0       0       0       0       0       0       0       0   
9        0        0       0       0       0       0       0       0       0   

   2/8/20  2/9/20  2/10/20  2/11/20  2/12/20  2/13/20  2/14/20  2/15/20  \
0       0       0        0        0        0        0        0        0   
1       0       0        0        0        0        0        0        0   
2       0       0        0        0        0        0        0        0   
3       0       0        0        0        0        0        0        0   
4       0       0        0        0        0        0        0        0   
5       0       0        0        0        0        0        0        0   
6       0       0        0        0        0        0        0        0   
7       0       0        0        0        0        0        0        0   
8       0       0        0        0        0        0        0        0   
9       0       0        0        0        0        0        0        0   

   2/16/20  2/17/20  2/18/20  2/19/20  2/20/20  2/21/20  2/22/20  2/23/20  \
0        0        0        0        0        0        0        0        0   
1        0        0        0        0        0        0        0        0   
2        0        0        0        0        0        0        0        0   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   
5        0        0        0        0        0        0        0        0   
6        0        0        0        0        0        0        0        0   
7        0        0        0   



--- Acummulated Number of Recovered Cases Worlwide ---



Province/State       Country/Region      Lat      Long  \
0                           NaN          Afghanistan  33.0000   65.0000   
1                           NaN              Albania  41.1533   20.1683   
2                           NaN              Algeria  28.0339    1.6596   
3                           NaN              Andorra  42.5063    1.5218   
4                           NaN               Angola -11.2027   17.8739   
5                           NaN  Antigua and Barbuda  17.0608  -61.7964   
6                           NaN            Argentina -38.4161  -63.6167   
7                           NaN              Armenia  40.0691   45.0382   
8  Australian Capital Territory            Australia -35.4735  149.0124   
9               New South Wales            Australia -33.8688  151.2093   

   1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  1/27/20  1/28/20  1/29/20  \
0        0        0        0        0        0        0        0        0   
1        0        0        0        0        0        0        0        0   
2        0        0        0        0        0        0        0        0   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   
5        0        0        0        0        0        0        0        0   
6        0        0        0        0        0        0        0        0   
7        0        0        0        0        0        0        0        0   
8        0        0        0        0        0        0        0        0   
9        0        0        0        0        0        0        0        0   

   1/30/20  1/31/20  2/1/20  2/2/20  2/3/20  2/4/20  2/5/20  2/6/20  2/7/20  \
0        0        0       0       0       0       0       0       0       0   
1        0        0       0       0       0       0       0       0       0   
2        0        0       0       0       0       0       0       0       0   
3        0        0       0       0       0       0       0       0       0   
4        0        0       0       0       0       0       0       0       0   
5        0        0       0       0       0       0       0       0       0   
6        0        0       0       0       0       0       0       0       0   
7        0        0       0       0       0       0       0       0       0   
8        0        0       0       0       0       0       0       0       0   
9        2        2       2       2       2       2       2       2       2   

   2/8/20  2/9/20  2/10/20  2/11/20  2/12/20  2/13/20  2/14/20  2/15/20  \
0       0       0        0        0        0        0        0        0   
1       0       0        0        0        0        0        0        0   
2       0       0        0        0        0        0        0        0   
3       0       0        0        0        0        0        0        0   
4       0       0        0        0        0        0        0        0   
5       0       0        0        0        0        0        0        0   
6       0       0        0        0        0        0        0        0   
7       0       0        0        0        0        0        0        0   
8       0       0        0        0        0        0        0        0   
9       2       2        2        2        2        4        4        4   

   2/16/20  2/17/20  2/18/20  2/19/20  2/20/20  2/21/20  2/22/20  2/23/20  \
0        0        0        0        0        0        0        0        0   
1        0        0        0        0        0        0        0        0   
2        0        0        0        0        0        0        0        0   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   
5        0        0        0        0        0        0        0        0   
6        0        0        0        0        0        0        0        0   
7        0        0        0   

> ### B.2.2 Dataframes regarding countries' additional demographic data

In [0]:
print("\n--- Countries' Demographic Data and Income Group (Classified by 'The World Bank')---\n")
display(countries_df.head(10))
print('\nData Types:\n')
display(countries_df.dtypes)

print("\n\n\n\n--- Countries' ISO Alpha-2 Codes ---\n\n")
display(alpha_2.head(10))
print('\nData Types:\n')
display(alpha_2.dtypes)


--- Countries' Demographic Data and Income Group (Classified by 'The World Bank')---



Code        Country  CurrentPopulation        Area    Density  GrowthRate  \
0   CN          China        1439323.776   9706961.0   148.2775      1.0039   
1   IN          India        1380004.385   3287590.0   419.7617      1.0099   
2   US  United States         331002.651   9372610.0    35.3160      1.0059   
3   ID      Indonesia         273523.615   1904569.0   143.6144      1.0107   
4   PK       Pakistan         220892.340    881912.0   250.4698      1.0200   
5   BR         Brazil         212559.417   8515767.0    24.9607      1.0072   
6   NG        Nigeria         206139.589    923768.0   223.1508      1.0258   
7   BD     Bangladesh         164689.383    147570.0  1116.0086      1.0101   
8   RU         Russia         145934.462  17098242.0     8.5351      1.0004   
9   MX         Mexico         128932.753   1964375.0    65.6355      1.0106   

   WorldPercentage                     Region         Income group  
0           0.1847        East Asia & Pacific  Upper middle income  
1           0.1770                 South Asia  Lower middle income  
2           0.0425              North America          High income  
3           0.0351        East Asia & Pacific  Lower middle income  
4           0.0283                 South Asia  Lower middle income  
5           0.0273  Latin America & Caribbean  Upper middle income  
6           0.0264         Sub-Saharan Africa  Lower middle income  
7           0.0211                 South Asia  Lower middle income  
8           0.0187      Europe & Central Asia  Upper middle income  
9           0.0165  Latin America & Caribbean  Upper middle income


Data Types:



Code                  object
Country               object
CurrentPopulation    float64
Area                 float64
Density              float64
GrowthRate           float64
WorldPercentage      float64
Region                object
Income group          object
dtype: object





--- Countries' ISO Alpha-2 Codes ---




Country cca2
0          Afghanistan   AF
1              Albania   AL
2              Algeria   DZ
3              Andorra   AD
4               Angola   AO
5  Antigua and Barbuda   AG
6            Argentina   AR
7              Armenia   AM
8            Australia   AU
9              Austria   AT


Data Types:



Country    object
cca2       object
dtype: object

### **B.3** Grouping countries together in order exclude the 'Province/State' level of granularity, since most of this feature's values are missing (NaN). 
> It is relevant to point out that, by performing the previously mentioned action, all countries' territories were added together with their corresponding mother lands. With this in view, for example, French Guiana and France are regarded as the same land.

##### For each country's features, the following **aggregate functions** were used:


*   Latitude ('Lat'): average (numpy's mean)
*   Longitude ('Long'): average (numpy's mean)
*   Remaining numerical features: sum 





In [0]:
grp_confirmed = pd.concat([confirmed_df.iloc[:,1:4].groupby(by='Country/Region').agg({'Lat':np.mean,'Long':np.mean,}).reset_index(),
                           confirmed_df.groupby(by='Country/Region').sum().reset_index().iloc[:,3:]],
                           axis=1
                         )
confirmed = grp_confirmed.copy()

grp_deaths = pd.concat([deaths_df.iloc[:,1:4].groupby(by='Country/Region').agg({'Lat':np.mean,'Long':np.mean,}).reset_index(),
                        deaths_df.groupby(by='Country/Region').sum().reset_index().iloc[:,3:]],
                        axis=1
                      )
deaths = grp_deaths.copy()

grp_recoveries = pd.concat([recoveries_df.iloc[:,1:4].groupby(by='Country/Region').agg({'Lat':np.mean,'Long':np.mean,}).reset_index(),
                           recoveries_df.groupby(by='Country/Region').sum().reset_index().iloc[:,3:]],
                           axis=1
                          )
recoveries = grp_recoveries.copy()

> ### B.3.1 Checking shapes and heads of the three grouped dataframes

In [0]:
print('--- Grouped Confirmed Cases ---\n Shape:', grp_confirmed.shape)
display(grp_confirmed.head(10))
print('\n\n--- Grouped Deaths ---\n Shape:', grp_deaths.shape)
display(grp_deaths.head(10))
print('\n\n--- Grouped Recovered Cases ---\n Shape:', grp_recoveries.shape)
display(grp_recoveries.head(10))

--- Grouped Confirmed Cases ---
 Shape: (188, 127)


Country/Region        Lat        Long  1/22/20  1/23/20  1/24/20  \
0          Afghanistan  33.000000   65.000000        0        0        0   
1              Albania  41.153300   20.168300        0        0        0   
2              Algeria  28.033900    1.659600        0        0        0   
3              Andorra  42.506300    1.521800        0        0        0   
4               Angola -11.202700   17.873900        0        0        0   
5  Antigua and Barbuda  17.060800  -61.796400        0        0        0   
6            Argentina -38.416100  -63.616700        0        0        0   
7              Armenia  40.069100   45.038200        0        0        0   
8            Australia -31.996188  141.232788        0        0        0   
9              Austria  47.516200   14.550100        0        0        0   

   1/25/20  1/26/20  1/27/20  1/28/20  1/29/20  1/30/20  1/31/20  2/1/20  \
0        0        0        0        0        0        0        0       0   
1        0        0        0        0        0        0        0       0   
2        0        0        0        0        0        0        0       0   
3        0        0        0        0        0        0        0       0   
4        0        0        0        0        0        0        0       0   
5        0        0        0        0        0        0        0       0   
6        0        0        0        0        0        0        0       0   
7        0        0        0        0        0        0        0       0   
8        0        4        5        5        6        9        9      12   
9        0        0        0        0        0        0        0       0   

   2/2/20  2/3/20  2/4/20  2/5/20  2/6/20  2/7/20  2/8/20  2/9/20  2/10/20  \
0       0       0       0       0       0       0       0       0        0   
1       0       0       0       0       0       0       0       0        0   
2       0       0       0       0       0       0       0       0        0   
3       0       0       0       0       0       0       0       0        0   
4       0       0       0       0       0       0       0       0        0   
5       0       0       0       0       0       0       0       0        0   
6       0       0       0       0       0       0       0       0        0   
7       0       0       0       0       0       0       0       0        0   
8      12      12      13      13      14      15      15      15       15   
9       0       0       0       0       0       0       0       0        0   

   2/11/20  2/12/20  2/13/20  2/14/20  2/15/20  2/16/20  2/17/20  2/18/20  \
0        0        0        0        0        0        0        0        0   
1        0        0        0        0        0        0        0        0   
2        0        0        0        0        0        0        0        0   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   
5        0        0        0        0        0        0        0        0   
6        0        0        0        0        0        0        0        0   
7        0        0        0        0        0        0        0        0   
8       15       15       15       15       15       15       15       15   
9        0        0        0        0        0        0        0        0   

   2/19/20  2/20/20  2/21/20  2/22/20  2/23/20  2/24/20  2/25/20  2/26/20  \
0        0        0        0        0        0        1        1        1   
1        0        0        0        0        0        0        0        0   
2        0        0        0        0        0        0        1        1   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   
5        0        0        0        0        0        0        0        0   
6        0        0        0        0        0        0        0        0   
7        0 



--- Grouped Deaths ---
 Shape: (188, 127)


Country/Region        Lat        Long  1/22/20  1/23/20  1/24/20  \
0          Afghanistan  33.000000   65.000000        0        0        0   
1              Albania  41.153300   20.168300        0        0        0   
2              Algeria  28.033900    1.659600        0        0        0   
3              Andorra  42.506300    1.521800        0        0        0   
4               Angola -11.202700   17.873900        0        0        0   
5  Antigua and Barbuda  17.060800  -61.796400        0        0        0   
6            Argentina -38.416100  -63.616700        0        0        0   
7              Armenia  40.069100   45.038200        0        0        0   
8            Australia -31.996188  141.232788        0        0        0   
9              Austria  47.516200   14.550100        0        0        0   

   1/25/20  1/26/20  1/27/20  1/28/20  1/29/20  1/30/20  1/31/20  2/1/20  \
0        0        0        0        0        0        0        0       0   
1        0        0        0        0        0        0        0       0   
2        0        0        0        0        0        0        0       0   
3        0        0        0        0        0        0        0       0   
4        0        0        0        0        0        0        0       0   
5        0        0        0        0        0        0        0       0   
6        0        0        0        0        0        0        0       0   
7        0        0        0        0        0        0        0       0   
8        0        0        0        0        0        0        0       0   
9        0        0        0        0        0        0        0       0   

   2/2/20  2/3/20  2/4/20  2/5/20  2/6/20  2/7/20  2/8/20  2/9/20  2/10/20  \
0       0       0       0       0       0       0       0       0        0   
1       0       0       0       0       0       0       0       0        0   
2       0       0       0       0       0       0       0       0        0   
3       0       0       0       0       0       0       0       0        0   
4       0       0       0       0       0       0       0       0        0   
5       0       0       0       0       0       0       0       0        0   
6       0       0       0       0       0       0       0       0        0   
7       0       0       0       0       0       0       0       0        0   
8       0       0       0       0       0       0       0       0        0   
9       0       0       0       0       0       0       0       0        0   

   2/11/20  2/12/20  2/13/20  2/14/20  2/15/20  2/16/20  2/17/20  2/18/20  \
0        0        0        0        0        0        0        0        0   
1        0        0        0        0        0        0        0        0   
2        0        0        0        0        0        0        0        0   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   
5        0        0        0        0        0        0        0        0   
6        0        0        0        0        0        0        0        0   
7        0        0        0        0        0        0        0        0   
8        0        0        0        0        0        0        0        0   
9        0        0        0        0        0        0        0        0   

   2/19/20  2/20/20  2/21/20  2/22/20  2/23/20  2/24/20  2/25/20  2/26/20  \
0        0        0        0        0        0        0        0        0   
1        0        0        0        0        0        0        0        0   
2        0        0        0        0        0        0        0        0   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   
5        0        0        0        0        0        0        0        0   
6        0        0        0        0        0        0        0        0   
7        0 



--- Grouped Recovered Cases ---
 Shape: (188, 127)


Country/Region        Lat        Long  1/22/20  1/23/20  1/24/20  \
0          Afghanistan  33.000000   65.000000        0        0        0   
1              Albania  41.153300   20.168300        0        0        0   
2              Algeria  28.033900    1.659600        0        0        0   
3              Andorra  42.506300    1.521800        0        0        0   
4               Angola -11.202700   17.873900        0        0        0   
5  Antigua and Barbuda  17.060800  -61.796400        0        0        0   
6            Argentina -38.416100  -63.616700        0        0        0   
7              Armenia  40.069100   45.038200        0        0        0   
8            Australia -31.996188  141.232788        0        0        0   
9              Austria  47.516200   14.550100        0        0        0   

   1/25/20  1/26/20  1/27/20  1/28/20  1/29/20  1/30/20  1/31/20  2/1/20  \
0        0        0        0        0        0        0        0       0   
1        0        0        0        0        0        0        0       0   
2        0        0        0        0        0        0        0       0   
3        0        0        0        0        0        0        0       0   
4        0        0        0        0        0        0        0       0   
5        0        0        0        0        0        0        0       0   
6        0        0        0        0        0        0        0       0   
7        0        0        0        0        0        0        0       0   
8        0        0        0        0        0        2        2       2   
9        0        0        0        0        0        0        0       0   

   2/2/20  2/3/20  2/4/20  2/5/20  2/6/20  2/7/20  2/8/20  2/9/20  2/10/20  \
0       0       0       0       0       0       0       0       0        0   
1       0       0       0       0       0       0       0       0        0   
2       0       0       0       0       0       0       0       0        0   
3       0       0       0       0       0       0       0       0        0   
4       0       0       0       0       0       0       0       0        0   
5       0       0       0       0       0       0       0       0        0   
6       0       0       0       0       0       0       0       0        0   
7       0       0       0       0       0       0       0       0        0   
8       2       2       2       2       2       2       2       2        2   
9       0       0       0       0       0       0       0       0        0   

   2/11/20  2/12/20  2/13/20  2/14/20  2/15/20  2/16/20  2/17/20  2/18/20  \
0        0        0        0        0        0        0        0        0   
1        0        0        0        0        0        0        0        0   
2        0        0        0        0        0        0        0        0   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   
5        0        0        0        0        0        0        0        0   
6        0        0        0        0        0        0        0        0   
7        0        0        0        0        0        0        0        0   
8        2        2        8        8        8        8       10       10   
9        0        0        0        0        0        0        0        0   

   2/19/20  2/20/20  2/21/20  2/22/20  2/23/20  2/24/20  2/25/20  2/26/20  \
0        0        0        0        0        0        0        0        0   
1        0        0        0        0        0        0        0        0   
2        0        0        0        0        0        0        0        0   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   
5        0        0        0        0        0        0        0        0   
6        0        0        0        0        0        0        0        0   
7        0 

# C. **Methodology**

> In an effort to meet this project's goals, the k-means clustering algorithm was used, aiming at detecting similarities in terms of how the disease is evolving worlwide amongst the diffent countries. To find a good k value (number of clusters) in order to run k-means, the Elbow Method was applied three times, namely, for the countries' confirmed cases, deaths and recoveries times series.


> Possessing the three k values, the k-means clustering algorithm progressed by fitting the scaled (with MinMaxScaler) numerical data and yelding the corresponding cluster labels. The three cluster labels series were, then, inserted into three target dataframes, each one corresponding to one category (confirmed, deaths and recoveries).

> New categorical features were, then, added into the dataframes to further enrich subsequent analysis. Some of those new features are country's current population, area and demographic density.

> From the three above dataframes, one unified dataframe was produced, containing the current values of confirmed cases, deaths and recoveries data, by country, as well as three new features: active cases, mortality rate and recovery rate, for each of the countries

### **C.1** Scaling each of the features (days' data points) using sklearn's MinMaxScaler, with the purpose of evenly weighting the features amongst themselves, as an attempt to decrease bias in the clustering process

In [0]:
for i in range(3, len(grp_confirmed.columns)):
  grp_confirmed.iloc[:,i]  = MinMaxScaler().fit_transform(grp_confirmed.iloc[:,i].values.reshape(-1,1))

for i in range(3, len(grp_deaths.columns)):
  grp_deaths.iloc[:,i] = MinMaxScaler().fit_transform(grp_deaths.iloc[:,i].values.reshape(-1,1))

for i in range(3, len(grp_recoveries.columns)):
  grp_recoveries.iloc[:,i] = MinMaxScaler().fit_transform(grp_recoveries.iloc[:,i].values.reshape(-1,1))

### **C.2** Dropping the categorical features on each of the three grouped data frames, in order to enable k-means algorithm to run. Also checking the heads of the three purely numerical new data frames

In [0]:
x_confirmed = grp_confirmed.iloc[:, 3:]
display(x_confirmed.head())


x_deaths = grp_deaths.iloc[:, 3:]
display(x_deaths.head())

x_recoveries = grp_recoveries.iloc[:, 3:]
display(x_recoveries.head())

1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  1/27/20  1/28/20  1/29/20  \
0      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
1      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   1/30/20  1/31/20  2/1/20  2/2/20  2/3/20  2/4/20  2/5/20  2/6/20  2/7/20  \
0      0.0      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
1      0.0      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
2      0.0      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
3      0.0      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
4      0.0      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   

   2/8/20  2/9/20  2/10/20  2/11/20  2/12/20  2/13/20  2/14/20  2/15/20  \
0     0.0     0.0      0.0      0.0      0.0      0.0      0.0      0.0   
1     0.0     0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2     0.0     0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3     0.0     0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4     0.0     0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   2/16/20  2/17/20  2/18/20  2/19/20  2/20/20  2/21/20  2/22/20  2/23/20  \
0      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
1      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

    2/24/20   2/25/20   2/26/20   2/27/20   2/28/20   2/29/20    3/1/20  \
0  0.000013  0.000013  0.000013  0.000013  0.000013  0.000013  0.000013   
1  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2  0.000000  0.000013  0.000013  0.000013  0.000013  0.000013  0.000013   
3  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
4  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   

     3/2/20    3/3/20    3/4/20    3/5/20    3/6/20    3/7/20    3/8/20  \
0  0.000012  0.000012  0.000012  0.000012  0.000012  0.000012  0.000049   
1  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2  0.000037  0.000062  0.000149  0.000149  0.000211  0.000210  0.000235   
3  0.000012  0.000012  0.000012  0.000012  0.000012  0.000012  0.000012   
4  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   

     3/9/20   3/10/20   3/11/20   3/12/20   3/13/20   3/14/20   3/15/20  \
0  0.000049  0.000062  0.000087  0.000086  0.000086  0.000136  0.000198   
1  0.000025  0.000124  0.000148  0.000284  0.000408  0.000469  0.000518   
2  0.000247  0.000247  0.000247  0.000297  0.000321  0.000457  0.000593   
3  0.000012  0.000012  0.000012  0.000012  0.000012  0.000012  0.000012   
4  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   

    3/16/20   3/17/20   3/18/20   3/19/20   3/20/20   3/21/20   3/22/20  \
0  0.000259  0.000271  0.000271  0.000271  0.000295  0.000295  0.000491   
1  0.000629  0.000679  0.000727  0.000789  0.000862  0.000935  0.001093   
2  0.000666  0.000740  0.000912  0.001072  0.001108  0.001710  0.002468   
3  0.000025  0.000481  0.000481  0.000653  0.000923  0.001082  0.001388   
4  0.000000  0.000000  0.000000  0.000000  0.000012  0.000025  0.000025   

    3/23/20   3/24/20   3/25/20   3/26/20   3/27/20   3/28/20   3/29/20  \
0  0.000491  0.000907  0.001029  0.001121  0.001079  0.000903  0.000852   
1  0.001276  0.001508  0.001788  0.002075  0.001824  0.001618  0.001505   
2  0.002822  0.003236  0.003698  0.004378  0.004011  0.003728  0.003626   
3  0.001632  0.002010  0.002302  0.002672  0.00

1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  1/27/20  1/28/20  1/29/20  \
0      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
1      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   1/30/20  1/31/20  2/1/20  2/2/20  2/3/20  2/4/20  2/5/20  2/6/20  2/7/20  \
0      0.0      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
1      0.0      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
2      0.0      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
3      0.0      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
4      0.0      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   

   2/8/20  2/9/20  2/10/20  2/11/20  2/12/20  2/13/20  2/14/20  2/15/20  \
0     0.0     0.0      0.0      0.0      0.0      0.0      0.0      0.0   
1     0.0     0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2     0.0     0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3     0.0     0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4     0.0     0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   2/16/20  2/17/20  2/18/20  2/19/20  2/20/20  2/21/20  2/22/20  2/23/20  \
0      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
1      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   2/24/20  2/25/20  2/26/20  2/27/20  2/28/20  2/29/20  3/1/20  3/2/20  \
0      0.0      0.0      0.0      0.0      0.0      0.0     0.0     0.0   
1      0.0      0.0      0.0      0.0      0.0      0.0     0.0     0.0   
2      0.0      0.0      0.0      0.0      0.0      0.0     0.0     0.0   
3      0.0      0.0      0.0      0.0      0.0      0.0     0.0     0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0     0.0     0.0   

   3/3/20  3/4/20  3/5/20  3/6/20  3/7/20  3/8/20  3/9/20  3/10/20   3/11/20  \
0     0.0     0.0     0.0     0.0     0.0     0.0     0.0      0.0  0.000000   
1     0.0     0.0     0.0     0.0     0.0     0.0     0.0      0.0  0.000316   
2     0.0     0.0     0.0     0.0     0.0     0.0     0.0      0.0  0.000000   
3     0.0     0.0     0.0     0.0     0.0     0.0     0.0      0.0  0.000000   
4     0.0     0.0     0.0     0.0     0.0     0.0     0.0      0.0  0.000000   

    3/12/20   3/13/20   3/14/20   3/15/20   3/16/20   3/17/20   3/18/20  \
0  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
1  0.000315  0.000314  0.000313  0.000312  0.000311  0.000310  0.000617   
2  0.000315  0.000629  0.000940  0.001249  0.001243  0.001238  0.002160   
3  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
4  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   

    3/19/20   3/20/20   3/21/20   3/22/20   3/23/20   3/24/20   3/25/20  \
0  0.000000  0.000000  0.000000  0.000183  0.000165  0.000147  0.000267   
1  0.000587  0.000496  0.000415  0.000365  0.000658  0.000733  0.000666   
2  0.002643  0.002728  0.003109  0.003104  0.002797  0.002786  0.002799   
3  0.000000  0.000000  0.000000  0.000183  0.000165  0.000147  0.000133   
4  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   

    3/26/20   3/27/20   3/28/20   3/29/20   3/30/20   3/31/20    4/1/20  \
0  0.000487  0.000438  0.000399  0.000371  0.000345  0.000322  0.000304   
1  0.000730  0.000876  0.000998  0.000928  0.000949  0.001207  0.001140   
2  0.003043  0.002847  0.002893  0.002876  0.003020  0.003540  0.004409   
3  0.000365  0.00

1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  1/27/20  1/28/20  1/29/20  \
0      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
1      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   1/30/20  1/31/20  2/1/20  2/2/20  2/3/20  2/4/20  2/5/20  2/6/20  2/7/20  \
0      0.0      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
1      0.0      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
2      0.0      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
3      0.0      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
4      0.0      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   

   2/8/20  2/9/20  2/10/20  2/11/20  2/12/20  2/13/20  2/14/20  2/15/20  \
0     0.0     0.0      0.0      0.0      0.0      0.0      0.0      0.0   
1     0.0     0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2     0.0     0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3     0.0     0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4     0.0     0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   2/16/20  2/17/20  2/18/20  2/19/20  2/20/20  2/21/20  2/22/20  2/23/20  \
0      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
1      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   2/24/20  2/25/20  2/26/20  2/27/20  2/28/20  2/29/20  3/1/20  3/2/20  \
0      0.0      0.0      0.0      0.0      0.0      0.0     0.0     0.0   
1      0.0      0.0      0.0      0.0      0.0      0.0     0.0     0.0   
2      0.0      0.0      0.0      0.0      0.0      0.0     0.0     0.0   
3      0.0      0.0      0.0      0.0      0.0      0.0     0.0     0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0     0.0     0.0   

   3/3/20  3/4/20  3/5/20  3/6/20  3/7/20  3/8/20  3/9/20  3/10/20  3/11/20  \
0     0.0     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0   
1     0.0     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0   
2     0.0     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0   
3     0.0     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0   
4     0.0     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0   

    3/12/20   3/13/20   3/14/20   3/15/20   3/16/20   3/17/20   3/18/20  \
0  0.000000  0.000000  0.000000  0.000000  0.000015  0.000015  0.000014   
1  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2  0.000127  0.000125  0.000183  0.000179  0.000177  0.000174  0.000172   
3  0.000016  0.000000  0.000015  0.000015  0.000015  0.000015  0.000014   
4  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   

    3/19/20   3/20/20   3/21/20   3/22/20   3/23/20   3/24/20   3/25/20  \
0  0.000014  0.000014  0.000014  0.000014  0.000014  0.000014  0.000027   
1  0.000000  0.000000  0.000028  0.000028  0.000027  0.000136  0.000230   
2  0.000454  0.000449  0.000445  0.000898  0.000893  0.000328  0.000881   
3  0.000014  0.000014  0.000014  0.000014  0.000014  0.000014  0.000014   
4  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   

    3/26/20   3/27/20   3/28/20   3/29/20   3/30/20   3/31/20    4/1/20  \
0  0.000027  0.000027  0.000027  0.000026  0.000026  0.000066  0.000065   
1  0.000229  0.000415  0.000413  0.000437  0.000580  0.000682  0.000877   
2  0.000391  0.000388  0.000413  0.000410  0.000487  0.000604  0.000798   
3  0.000013  0.000013  

### **C.3** Making use of **k-means Clustering**  algorithm as a way to group together different countries based on their time series' similarities for the Confirmed Cases data, Deaths data and Recoveries data times series

> ###### Defining the **'ElbowMethod'** function to determine the desired k-value for the k-means algorithm. The function aims to:

*   Determine the best number of clusters for a dataset (df) given a range of cluster values (Ks) to be tested by the Elbow Method;

*   Plot the sum of squared distances (SSD) versus the the k-values in the range Ks and highlights the optimal k-value in the plot;

*   Fit the model given the k-value;

*   Concatenate the predicted values (labels) column-wise into a targeted dataframe.




In [0]:
def ElbowMethod(df, target_df, Ks=15):

  #finding ssd value for every k
  ssd = []
  K = range(1,Ks+1)
  for k in K:
    km = KMeans(init='k-means++', n_clusters=k, n_init = 3, n_jobs = -1, random_state=0).fit(df)
    ssd.append(km.inertia_)
    
  #define the best k (step in ssd < 1)
  #ssd_ = [ssd[i] - ssd[i+1] for i in range(0, len(ssd)-1)]
  #k_value = [index for index,value in enumerate(ssd_) if value < 1][0]+1

  #max distance method to identify the best k 
  import math as m
  x1, y1 = 1, ssd[0]
  x2, y2 = Ks+1, ssd[-1]

  distances = []
  for i in range(len(ssd)):
        x0 = i+1
        y0 = ssd[i]
        numerator = abs((y2-y1)*x0 - (x2-x1)*y0 + x2*y1 - y2*x1)
        denominator = m.sqrt((y2 - y1)**2 + (x2 - x1)**2)
        distances.append(numerator/denominator)
    
  k_value=distances.index(max(distances)) + 1

  #plotting the values of ssd versus k

  df_plot = pd.DataFrame({'k-values': K, 'SSD': ssd})
  #additional importing of lib to avoid bugs
  import plotly.express as px 
  fig = px.line(df_plot, x='k-values',
                   y='SSD',
                   title='Elbow Method Graphing',
                  
                   )
  
  #highlighting k-value in the plot
  fig.update_layout(shapes=[
    dict(
      type= 'line',
      yref= 'paper', y0= 0, y1= 1,
      xref= 'x', x0= k_value, x1= k_value,
      line=dict(dash='dot', color='LightSeaGreen')
    )
    
  ])
  
  fig.update_layout(
    showlegend=False,
    annotations=[
        dict(
            x=k_value,
            y=np.asarray(ssd).mean()+50,
            xref="x",
            yref="y",
            text="Desired k-value",
            showarrow=False,
            arrowhead=7,
            ax=0,
            ay=-40
        )
    ]
  )
  fig.update_layout(
    xaxis=dict(showgrid=False, zeroline=True),
    yaxis=dict(showgrid=True, zeroline=True),
  )
  fig.update_xaxes(tick0=0, dtick=1)
  fig.show()

  #fitting the model and concatenating predicted values into target_df
  kmeans = KMeans(init='k-means++', n_clusters=k_value, n_init = 3, n_jobs = -1).fit(df)
  target_df.insert(0, 'Cluster Labels', kmeans.labels_)

> ### C.3.1 Using the aforementioned function to graph the Elbow Method, fit the model and predict the labels for the confirmed cases, deaths and recoveries

In [0]:
'''Confirmed'''

ElbowMethod(x_confirmed, confirmed)

In [0]:
'''Deaths'''

ElbowMethod(x_deaths, deaths)

In [0]:
'''Recoveries'''

ElbowMethod(x_recoveries, recoveries)

### **C.4** Computing additional categorical features into the dataframes confirmed_data, deaths_data and recoveries_data, to further enrich subsequent analysis. Some of those new features, for each of the countries, are:

*   Current population;
*   Area;
*   Demographic density;
*   Region;
*   Income group (Classified by The World Bank);



> ###### Defining a function to add the aforementioned features and standardize the dataframes' structures

In [0]:
def MergeStd(df):

  '''Merge new features into df and standardize its columns'''

  temp_df = pd.merge(df, alpha_2, how='left', left_on='Country/Region', right_on='Country')
  temp_df = pd.merge(countries_df, temp_df, how='outer', left_on='Code', right_on='cca2')
  temp_df.dropna(inplace=True)
  temp_df.drop(list(temp_df.columns[-2:])+list(temp_df.columns[10:11]), axis=1, inplace=True)
  temp_df.rename({'Country_x':'Country'}, axis=1, inplace=True)
  temp_df['CurrentPopulation'] = temp_df['CurrentPopulation']*np.power(10,3)
  temp_df.reset_index(inplace=True, drop=True)

  return temp_df

### **C.5** Cluster Labeled dataframes

> ### C.5.1 Labeled Confirmed Cases Time Series

In [0]:
confirmed_data = MergeStd(confirmed)

In [0]:
confirmed_data.head()

Code        Country  CurrentPopulation       Area   Density  GrowthRate  \
0   CN          China       1.439324e+09  9706961.0  148.2775      1.0039   
1   IN          India       1.380004e+09  3287590.0  419.7617      1.0099   
2   US  United States       3.310027e+08  9372610.0   35.3160      1.0059   
3   ID      Indonesia       2.735236e+08  1904569.0  143.6144      1.0107   
4   PK       Pakistan       2.208923e+08   881912.0  250.4698      1.0200   

   WorldPercentage               Region         Income group  Cluster Labels  \
0           0.1847  East Asia & Pacific  Upper middle income             2.0   
1           0.1770           South Asia  Lower middle income             0.0   
2           0.0425        North America          High income             1.0   
3           0.0351  East Asia & Pacific  Lower middle income             0.0   
4           0.0283           South Asia  Lower middle income             0.0   

         Lat        Long  1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  \
0  32.828385  111.649082    548.0    643.0    920.0   1406.0   2075.0   
1  21.000000   78.000000      0.0      0.0      0.0      0.0      0.0   
2  37.090200  -95.712900      1.0      1.0      2.0      2.0      5.0   
3  -0.789300  113.921300      0.0      0.0      0.0      0.0      0.0   
4  30.375300   69.345100      0.0      0.0      0.0      0.0      0.0   

   1/27/20  1/28/20  1/29/20  1/30/20  1/31/20   2/1/20   2/2/20   2/3/20  \
0   2877.0   5509.0   6087.0   8141.0   9802.0  11891.0  16630.0  19716.0   
1      0.0      0.0      0.0      1.0      1.0      1.0      2.0      3.0   
2      5.0      5.0      5.0      5.0      7.0      8.0      8.0     11.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

    2/4/20   2/5/20   2/6/20   2/7/20   2/8/20   2/9/20  2/10/20  2/11/20  \
0  23707.0  27440.0  30587.0  34110.0  36814.0  39829.0  42354.0  44386.0   
1      3.0      3.0      3.0      3.0      3.0      3.0      3.0      3.0   
2     11.0     11.0     11.0     11.0     11.0     11.0     11.0     12.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   2/12/20  2/13/20  2/14/20  2/15/20  2/16/20  2/17/20  2/18/20  2/19/20  \
0  44759.0  59895.0  66358.0  68413.0  70513.0  72434.0  74211.0  74619.0   
1      3.0      3.0      3.0      3.0      3.0      3.0      3.0      3.0   
2     12.0     13.0     13.0     13.0     13.0     13.0     13.0     13.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   2/20/20  2/21/20  2/22/20  2/23/20  2/24/20  2/25/20  2/26/20  2/27/20  \
0  75077.0  75550.0  77001.0  77022.0  77241.0  77754.0  78166.0  78600.0   
1      3.0      3.0      3.0      3.0      3.0      3.0      3.0      3.0   
2     13.0     15.0     15.0     15.0     51.0     51.0     57.0     58.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      2.0      2.0   

   2/28/20  2/29/20   3/1/20   3/2/20   3/3/20   3/4/20   3/5/20   3/6/20  \
0  78928.0  79356.0  79932.0  80136.0  80261.0  80386.0  80537.0  80690.0   
1      3.0      3.0      3.0      5.0      5.0     28.0     30.0     31.0   
2     60.0     68.0     74.0     98.0    118.0    149.0    219.0    267.0   
3      0.0      0.0      0.0      2.0      2.0      2.0      2.0      4.0   
4      2.0      4.0      4.0      4.0      5.0      5.0      5.0      6.0   

    3/7/20   3/8/20   3/9/20  3/10/20  3/11/20  3/12/20  3/13/20  3/14/20  \
0  80770.0  80823.0  80860.0  80887.0  80921.0  80932.0  80945.0  80977.0   
1     34.0     39.0     43.0     56.0     62.0     73.0     82.0    102.0   
2    403.0    519.0    588.0    962.0   1285.0   1667.0   2181.0   2729.0

In [0]:
confirmed_data.describe() #numerical data

CurrentPopulation          Area       Density  GrowthRate  \
count       1.800000e+02  1.800000e+02    180.000000  180.000000   
mean        4.268585e+07  7.295672e+05    314.812673    1.011952   
std         1.531813e+08  1.978080e+06   1577.076593    0.010822   
min         3.393100e+04  2.020000e+00      2.095900    0.986500   
25%         2.838920e+06  2.949425e+04     32.228875    1.003200   
50%         9.897504e+06  1.451405e+05     86.580950    1.010750   
75%         3.111856e+07  5.588630e+05    201.441325    1.019525   
max         1.439324e+09  1.709824e+07  19426.732700    1.038400   

       WorldPercentage  Cluster Labels         Lat        Long     1/22/20  \
count       180.000000      180.000000  180.000000  180.000000  180.000000   
mean          0.005477        0.100000   19.414931   16.868808    3.083333   
std           0.019652        0.518916   23.616660   58.043258   40.843327   
min           0.000000        0.000000  -40.900600 -102.552800    0.000000   
25%           0.000375        0.000000    5.114075   -9.496275    0.000000   
50%           0.001300        0.000000   17.589246   19.933650    0.000000   
75%           0.004000        0.000000   39.549925   45.009550    0.000000   
max           0.184700        3.000000   64.963100  178.065000  548.000000   

          1/23/20     1/24/20      1/25/20      1/26/20      1/27/20  \
count  180.000000  180.000000   180.000000   180.000000   180.000000   
mean     3.633333    5.227778     7.966667    11.766667    16.261111   
std     47.922995   68.566473   104.787996   154.646763   214.420913   
min      0.000000    0.000000     0.000000     0.000000     0.000000   
25%      0.000000    0.000000     0.000000     0.000000     0.000000   
50%      0.000000    0.000000     0.000000     0.000000     0.000000   
75%      0.000000    0.000000     0.000000     0.000000     0.000000   
max    643.000000  920.000000  1406.000000  2075.000000  2877.000000   

           1/28/20      1/29/20      1/30/20      1/31/20        2/1/20  \
count   180.000000   180.000000   180.000000   180.000000    180.000000   
mean     30.988889    34.255556    45.744444    55.150000     66.877778   
std     410.590990   453.668487   606.758842   730.550435    886.246644   
min       0.000000     0.000000     0.000000     0.000000      0.000000   
25%       0.000000     0.000000     0.000000     0.000000      0.000000   
50%       0.000000     0.000000     0.000000     0.000000      0.000000   
75%       0.000000     0.000000     0.000000     0.000000      0.000000   
max    5509.000000  6087.000000  8141.000000  9802.000000  11891.000000   

             2/2/20        2/3/20        2/4/20        2/5/20        2/6/20  \
count    180.000000    180.000000    180.000000    180.000000    180.000000   
mean      93.261111    110.450000    132.733333    153.527778    171.077778   
std     1239.465660   1469.478786   1766.942493   2045.179637   2279.738176   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      0.000000      0.000000   
75%        0.000000      0.000000      0.000000      0.000000      0.000000   
max    16630.000000  19716.000000  23707.000000  27440.000000  30587.000000   

             2/7/20        2/8/20        2/9/20       2/10/20       2/11/20  \
count    180.000000    180.000000    180.000000    180.000000    180.000000   
mean     190.722222    205.883333    222.700000    236.816667    248.150000   
std     2542.321668   2743.856087   2968.576182   3156.772193   3308.225296   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      0.000000      0.000000   
75%        0.000000      0.000000      0.000000      0.000000      0.000000   
max    34110.000000  3

> ### C.5.2 Labeled Deaths Time Series

In [0]:
deaths_data =  MergeStd(deaths)

In [0]:
deaths_data.head()

Code        Country  CurrentPopulation       Area   Density  GrowthRate  \
0   CN          China       1.439324e+09  9706961.0  148.2775      1.0039   
1   IN          India       1.380004e+09  3287590.0  419.7617      1.0099   
2   US  United States       3.310027e+08  9372610.0   35.3160      1.0059   
3   ID      Indonesia       2.735236e+08  1904569.0  143.6144      1.0107   
4   PK       Pakistan       2.208923e+08   881912.0  250.4698      1.0200   

   WorldPercentage               Region         Income group  Cluster Labels  \
0           0.1847  East Asia & Pacific  Upper middle income             2.0   
1           0.1770           South Asia  Lower middle income             0.0   
2           0.0425        North America          High income             3.0   
3           0.0351  East Asia & Pacific  Lower middle income             0.0   
4           0.0283           South Asia  Lower middle income             0.0   

         Lat        Long  1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  \
0  32.828385  111.649082     17.0     18.0     26.0     42.0     56.0   
1  21.000000   78.000000      0.0      0.0      0.0      0.0      0.0   
2  37.090200  -95.712900      0.0      0.0      0.0      0.0      0.0   
3  -0.789300  113.921300      0.0      0.0      0.0      0.0      0.0   
4  30.375300   69.345100      0.0      0.0      0.0      0.0      0.0   

   1/27/20  1/28/20  1/29/20  1/30/20  1/31/20  2/1/20  2/2/20  2/3/20  \
0     82.0    131.0    133.0    171.0    213.0   259.0   361.0   425.0   
1      0.0      0.0      0.0      0.0      0.0     0.0     0.0     0.0   
2      0.0      0.0      0.0      0.0      0.0     0.0     0.0     0.0   
3      0.0      0.0      0.0      0.0      0.0     0.0     0.0     0.0   
4      0.0      0.0      0.0      0.0      0.0     0.0     0.0     0.0   

   2/4/20  2/5/20  2/6/20  2/7/20  2/8/20  2/9/20  2/10/20  2/11/20  2/12/20  \
0   491.0   563.0   633.0   718.0   805.0   905.0   1012.0   1112.0   1117.0   
1     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0      0.0   
2     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0      0.0   
3     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0      0.0   
4     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0      0.0   

   2/13/20  2/14/20  2/15/20  2/16/20  2/17/20  2/18/20  2/19/20  2/20/20  \
0   1369.0   1521.0   1663.0   1766.0   1864.0   2003.0   2116.0   2238.0   
1      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   2/21/20  2/22/20  2/23/20  2/24/20  2/25/20  2/26/20  2/27/20  2/28/20  \
0   2238.0   2443.0   2445.0   2595.0   2665.0   2717.0   2746.0   2790.0   
1      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   2/29/20  3/1/20  3/2/20  3/3/20  3/4/20  3/5/20  3/6/20  3/7/20  3/8/20  \
0   2837.0  2872.0  2914.0  2947.0  2983.0  3015.0  3044.0  3072.0  3100.0   
1      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
2      1.0     1.0     6.0     7.0    11.0    12.0    14.0    17.0    21.0   
3      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
4      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   

   3/9/20  3/10/20  3/11/20  3/12/20  3/13/20  3/14/20  3/15/20  3/16/20  \
0  3123.0   3139.0   3161.0   3172.0   3180.0   3193.0   3203.0   3217.0   
1     0.0      0.0      1.0      1.0      2.0      2.0      2.0      2.0   
2    22.0     28.0     36.0     42.0     50.0     60.0     74.0    100

In [0]:
deaths_data.describe() #numerical data

CurrentPopulation          Area       Density  GrowthRate  \
count       1.800000e+02  1.800000e+02    180.000000  180.000000   
mean        4.268585e+07  7.295672e+05    314.812673    1.011952   
std         1.531813e+08  1.978080e+06   1577.076593    0.010822   
min         3.393100e+04  2.020000e+00      2.095900    0.986500   
25%         2.838920e+06  2.949425e+04     32.228875    1.003200   
50%         9.897504e+06  1.451405e+05     86.580950    1.010750   
75%         3.111856e+07  5.588630e+05    201.441325    1.019525   
max         1.439324e+09  1.709824e+07  19426.732700    1.038400   

       WorldPercentage  Cluster Labels         Lat        Long     1/22/20  \
count       180.000000      180.000000  180.000000  180.000000  180.000000   
mean          0.005477        0.050000   19.414931   16.868808    0.094444   
std           0.019652        0.304069   23.616660   58.043258    1.267105   
min           0.000000        0.000000  -40.900600 -102.552800    0.000000   
25%           0.000375        0.000000    5.114075   -9.496275    0.000000   
50%           0.001300        0.000000   17.589246   19.933650    0.000000   
75%           0.004000        0.000000   39.549925   45.009550    0.000000   
max           0.184700        3.000000   64.963100  178.065000   17.000000   

          1/23/20     1/24/20     1/25/20     1/26/20     1/27/20     1/28/20  \
count  180.000000  180.000000  180.000000  180.000000  180.000000  180.000000   
mean     0.100000    0.144444    0.233333    0.311111    0.455556    0.727778   
std      1.341641    1.937926    3.130495    4.173994    6.111919    9.764164   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
50%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
75%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
max     18.000000   26.000000   42.000000   56.000000   82.000000  131.000000   

          1/29/20     1/30/20     1/31/20      2/1/20      2/2/20      2/3/20  \
count  180.000000  180.000000  180.000000  180.000000  180.000000  180.000000   
mean     0.738889    0.950000    1.183333    1.438889    2.011111    2.366667   
std      9.913235   12.745587   15.876083   19.304720   26.907038   31.677301   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
50%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
75%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
max    133.000000  171.000000  213.000000  259.000000  361.000000  425.000000   

           2/4/20      2/5/20      2/6/20      2/7/20      2/8/20      2/9/20  \
count  180.000000  180.000000  180.000000  180.000000  180.000000  180.000000   
mean     2.733333    3.133333    3.522222    3.994444    4.477778    5.033333   
std     36.596639   41.963192   47.180677   53.516196   60.000787   67.454342   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
50%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
75%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
max    491.000000  563.000000  633.000000  718.000000  805.000000  905.000000   

           2/10/20      2/11/20      2/12/20      2/13/20      2/14/20  \
count   180.000000   180.000000   180.000000   180.000000   180.000000   
mean      5.627778     6.183333     6.211111     7.616667     8.461111   
std      75.429647    82.883203    83.255881   102.038457   113.367862   
min       0.000000     0.000000     0.000000     0.000000     0.000000   
25%       0.000000     0.000000     0.000000     0.000000     0.000000   
50%       0.000000     0.000000     0.000000     0.000000

> ### C.5.3 Labeled Recoveries Time Series

In [0]:
recoveries_data = MergeStd(recoveries)

In [0]:
recoveries_data.head()

Code        Country  CurrentPopulation       Area   Density  GrowthRate  \
0   CN          China       1.439324e+09  9706961.0  148.2775      1.0039   
1   IN          India       1.380004e+09  3287590.0  419.7617      1.0099   
2   US  United States       3.310027e+08  9372610.0   35.3160      1.0059   
3   ID      Indonesia       2.735236e+08  1904569.0  143.6144      1.0107   
4   PK       Pakistan       2.208923e+08   881912.0  250.4698      1.0200   

   WorldPercentage               Region         Income group  Cluster Labels  \
0           0.1847  East Asia & Pacific  Upper middle income             2.0   
1           0.1770           South Asia  Lower middle income             0.0   
2           0.0425        North America          High income             1.0   
3           0.0351  East Asia & Pacific  Lower middle income             0.0   
4           0.0283           South Asia  Lower middle income             0.0   

         Lat        Long  1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  \
0  32.828385  111.649082     28.0     30.0     36.0     39.0     49.0   
1  21.000000   78.000000      0.0      0.0      0.0      0.0      0.0   
2  37.090200  -95.712900      0.0      0.0      0.0      0.0      0.0   
3  -0.789300  113.921300      0.0      0.0      0.0      0.0      0.0   
4  30.375300   69.345100      0.0      0.0      0.0      0.0      0.0   

   1/27/20  1/28/20  1/29/20  1/30/20  1/31/20  2/1/20  2/2/20  2/3/20  \
0     58.0    101.0    120.0    135.0    214.0   275.0   463.0   614.0   
1      0.0      0.0      0.0      0.0      0.0     0.0     0.0     0.0   
2      0.0      0.0      0.0      0.0      0.0     0.0     0.0     0.0   
3      0.0      0.0      0.0      0.0      0.0     0.0     0.0     0.0   
4      0.0      0.0      0.0      0.0      0.0     0.0     0.0     0.0   

   2/4/20  2/5/20  2/6/20  2/7/20  2/8/20  2/9/20  2/10/20  2/11/20  2/12/20  \
0   843.0  1115.0  1477.0  1999.0  2596.0  3219.0   3918.0   4636.0   5082.0   
1     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0      0.0   
2     0.0     0.0     0.0     0.0     0.0     3.0      3.0      3.0      3.0   
3     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0      0.0   
4     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0      0.0   

   2/13/20  2/14/20  2/15/20  2/16/20  2/17/20  2/18/20  2/19/20  2/20/20  \
0   6217.0   7977.0   9298.0  10755.0  12462.0  14206.0  15962.0  18014.0   
1      0.0      0.0      0.0      3.0      3.0      3.0      3.0      3.0   
2      3.0      3.0      3.0      3.0      3.0      3.0      3.0      3.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   2/21/20  2/22/20  2/23/20  2/24/20  2/25/20  2/26/20  2/27/20  2/28/20  \
0  18704.0  22699.0  23187.0  25015.0  27676.0  30084.0  32930.0  36329.0   
1      3.0      3.0      3.0      3.0      3.0      3.0      3.0      3.0   
2      5.0      5.0      5.0      5.0      6.0      6.0      6.0      7.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   2/29/20   3/1/20   3/2/20   3/3/20   3/4/20   3/5/20   3/6/20   3/7/20  \
0  39320.0  42162.0  44854.0  47450.0  50001.0  52292.0  53944.0  55539.0   
1      3.0      3.0      3.0      3.0      3.0      3.0      3.0      3.0   
2      7.0      7.0      7.0      7.0      7.0      7.0      7.0      7.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

    3/8/20   3/9/20  3/10/20  3/11/20  3/12/20  3/13/20  3/14/20  3/15/20  \
0  57388.0  58804.0  60181.0  61644.0  62901.0  64196.0  65660.0  67017.0   
1      3.0      3.0      4.0      4.0      4.0      4.0      4.0     13.0   
2      7.0      7.0      8.0      8.0     12.0     12.0     12.0     12.0

In [0]:
recoveries_data.describe() #numerical data

CurrentPopulation          Area       Density  GrowthRate  \
count       1.800000e+02  1.800000e+02    180.000000  180.000000   
mean        4.268585e+07  7.295672e+05    314.812673    1.011952   
std         1.531813e+08  1.978080e+06   1577.076593    0.010822   
min         3.393100e+04  2.020000e+00      2.095900    0.986500   
25%         2.838920e+06  2.949425e+04     32.228875    1.003200   
50%         9.897504e+06  1.451405e+05     86.580950    1.010750   
75%         3.111856e+07  5.588630e+05    201.441325    1.019525   
max         1.439324e+09  1.709824e+07  19426.732700    1.038400   

       WorldPercentage  Cluster Labels         Lat        Long     1/22/20  \
count       180.000000      180.000000  180.000000  180.000000  180.000000   
mean          0.005477        0.038889   19.460195   16.769115    0.155556   
std           0.019652        0.220813   23.679444   58.240153    2.086997   
min           0.000000        0.000000  -40.900600 -106.346800    0.000000   
25%           0.000375        0.000000    5.114075   -9.496275    0.000000   
50%           0.001300        0.000000   17.589246   19.933650    0.000000   
75%           0.004000        0.000000   39.549925   45.009550    0.000000   
max           0.184700        2.000000   64.963100  178.065000   28.000000   

          1/23/20     1/24/20     1/25/20     1/26/20     1/27/20     1/28/20  \
count  180.000000  180.000000  180.000000  180.000000  180.000000  180.000000   
mean     0.166667    0.200000    0.216667    0.288889    0.338889    0.594444   
std      2.236068    2.683282    2.906888    3.654780    4.325014    7.535167   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
50%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
75%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
max     30.000000   36.000000   39.000000   49.000000   58.000000  101.000000   

          1/29/20     1/30/20     1/31/20      2/1/20      2/2/20      2/3/20  \
count  180.000000  180.000000  180.000000  180.000000  180.000000  180.000000   
mean     0.700000    0.794444    1.233333    1.577778    2.622222    3.461111   
std      8.949829   10.067203   15.952478   20.497705   34.508708   45.762975   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
50%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
75%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
max    120.000000  135.000000  214.000000  275.000000  463.000000  614.000000   

           2/4/20       2/5/20       2/6/20       2/7/20       2/8/20  \
count  180.000000   180.000000   180.000000   180.000000   180.000000   
mean     4.733333     6.244444     8.261111    11.172222    14.533333   
std     62.831121    83.104472   110.085714   148.992288   193.487701   
min      0.000000     0.000000     0.000000     0.000000     0.000000   
25%      0.000000     0.000000     0.000000     0.000000     0.000000   
50%      0.000000     0.000000     0.000000     0.000000     0.000000   
75%      0.000000     0.000000     0.000000     0.000000     0.000000   
max    843.000000  1115.000000  1477.000000  1999.000000  2596.000000   

            2/9/20      2/10/20      2/11/20      2/12/20      2/13/20  \
count   180.000000   180.000000   180.000000   180.000000   180.000000   
mean     18.022222    21.922222    26.016667    28.611111    34.972222   
std     239.921169   292.020173   345.530043   378.765318   463.359043   
min       0.000000     0.000000     0.000000     0.000000     0.000000   
25%       0.000000     0.000000     0.000000     0.000000     0.000000   
50%       0.000000     0.000000     0.000000     0.000000     0.000000   
75%       0.000000     0.000000     0.000000     0.0000

### **C.6** Processing the three above dataframes in order to produce one dataframe containing the current values of confirmed cases, deaths and recoveries data, by country. Adding, as well, three new features, for each of the $i$-th countries, which are:


*   $ActiveCases_{i} = (Confirmed_{i} - Deaths_{i} - Recoveries_{i})$

*   $MortalityRate_{i} = \frac{Deaths_{i}}{Confirmed_{i}}$

*   $RecoveryRate_{i} = \frac{Recoveries_{i}}{Confirmed_{i}}$



In [0]:
def ProduceCurrentData(df_c, df_d, df_r):

  #confirmed cases
  temp_c = df_c.copy() 
  #deaths
  temp_d = df_d.copy() 
  #recoveries
  temp_r = df_r.copy() 

  temp_dict = {'Confirmed': temp_c,
              'Deaths': temp_d,
              'Recoveries': temp_r
              }
  
  for item, value in zip(list(temp_dict), list(temp_dict.values())):
    value.rename({value.columns[-1]: str(item)}, axis=1, inplace=True)

  temp = pd.concat([temp_c.iloc[:, :9], temp_c.iloc[:, 10:12], temp_c.iloc[:,-1]], axis=1)
  temp = pd.concat([temp, temp_d.iloc[:,-1], temp_r.iloc[:,-1]], axis=1)
  temp['ActiveCases'] = temp['Confirmed'] - temp['Deaths'] - temp['Recoveries']
  temp['MortalityRate'] = temp['Deaths']/temp['Confirmed']
  temp['RecoveryRate'] = temp['Recoveries']/temp['Confirmed']

  return temp

In [0]:
current_data = ProduceCurrentData(confirmed_data, deaths_data, recoveries_data)

In [0]:
current_data.head()

Code        Country  CurrentPopulation       Area   Density  GrowthRate  \
0   CN          China       1.439324e+09  9706961.0  148.2775      1.0039   
1   IN          India       1.380004e+09  3287590.0  419.7617      1.0099   
2   US  United States       3.310027e+08  9372610.0   35.3160      1.0059   
3   ID      Indonesia       2.735236e+08  1904569.0  143.6144      1.0107   
4   PK       Pakistan       2.208923e+08   881912.0  250.4698      1.0200   

   WorldPercentage               Region         Income group        Lat  \
0           0.1847  East Asia & Pacific  Upper middle income  32.828385   
1           0.1770           South Asia  Lower middle income  21.000000   
2           0.0425        North America          High income  37.090200   
3           0.0351  East Asia & Pacific  Lower middle income  -0.789300   
4           0.0283           South Asia  Lower middle income  30.375300   

         Long  Confirmed   Deaths  Recoveries  ActiveCases  MortalityRate  \
0  111.649082    84095.0   4638.0     79343.0        114.0       0.055152   
1   78.000000   138536.0   4024.0     57692.0      76820.0       0.029047   
2  -95.712900  1643246.0  97720.0    366736.0    1178790.0       0.059468   
3  113.921300    22271.0   1372.0      5402.0      15497.0       0.061605   
4   69.345100    54601.0   1133.0     17198.0      36270.0       0.020751   

   RecoveryRate  
0      0.943492  
1      0.416440  
2      0.223178  
3      0.242558  
4      0.314976

In [0]:
current_data.dtypes

Code                  object
Country               object
CurrentPopulation    float64
Area                 float64
Density              float64
GrowthRate           float64
WorldPercentage      float64
Region                object
Income group          object
Lat                  float64
Long                 float64
Confirmed            float64
Deaths               float64
Recoveries           float64
ActiveCases          float64
MortalityRate        float64
RecoveryRate         float64
dtype: object

### **C.7** Creating three **non-cumulative** daily values dataframes: Confirmed Cases, Deaths and Recoveries 

> ###### Defining a function to create a non-acummulated daily values dataframe, starting from an acummulated daily values dataframe

In [0]:
def dailyNonCumulative(df):  
  
  temp_df = df.copy()

  for code in temp_df['Code'].unique():
    
    temp_list = []
    temp_slice = temp_df[temp_df['Code'] == code]
    daily_cases = temp_slice.iloc[0, 12:].tolist()

    for i, value in enumerate(daily_cases):
      if i == 0:
        temp_list.append(daily_cases[i])
      else:
        temp_list.append(daily_cases[i] - daily_cases[i-1])

    if len(temp_list) == len(daily_cases):
      temp_df.loc[(temp_df['Code'] == code), temp_df.columns[12:]] = temp_list

  return temp_df


> ### C.7.1 **Confirmed Cases** Dataframe

In [0]:
confirmed_daily = dailyNonCumulative(confirmed_data)

In [0]:
confirmed_daily.head()

Code        Country  CurrentPopulation       Area   Density  GrowthRate  \
0   CN          China       1.439324e+09  9706961.0  148.2775      1.0039   
1   IN          India       1.380004e+09  3287590.0  419.7617      1.0099   
2   US  United States       3.310027e+08  9372610.0   35.3160      1.0059   
3   ID      Indonesia       2.735236e+08  1904569.0  143.6144      1.0107   
4   PK       Pakistan       2.208923e+08   881912.0  250.4698      1.0200   

   WorldPercentage               Region         Income group  Cluster Labels  \
0           0.1847  East Asia & Pacific  Upper middle income             2.0   
1           0.1770           South Asia  Lower middle income             0.0   
2           0.0425        North America          High income             1.0   
3           0.0351  East Asia & Pacific  Lower middle income             0.0   
4           0.0283           South Asia  Lower middle income             0.0   

         Lat        Long  1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  \
0  32.828385  111.649082    548.0     95.0    277.0    486.0    669.0   
1  21.000000   78.000000      0.0      0.0      0.0      0.0      0.0   
2  37.090200  -95.712900      1.0      0.0      1.0      0.0      3.0   
3  -0.789300  113.921300      0.0      0.0      0.0      0.0      0.0   
4  30.375300   69.345100      0.0      0.0      0.0      0.0      0.0   

   1/27/20  1/28/20  1/29/20  1/30/20  1/31/20  2/1/20  2/2/20  2/3/20  \
0    802.0   2632.0    578.0   2054.0   1661.0  2089.0  4739.0  3086.0   
1      0.0      0.0      0.0      1.0      0.0     0.0     1.0     1.0   
2      0.0      0.0      0.0      0.0      2.0     1.0     0.0     3.0   
3      0.0      0.0      0.0      0.0      0.0     0.0     0.0     0.0   
4      0.0      0.0      0.0      0.0      0.0     0.0     0.0     0.0   

   2/4/20  2/5/20  2/6/20  2/7/20  2/8/20  2/9/20  2/10/20  2/11/20  2/12/20  \
0  3991.0  3733.0  3147.0  3523.0  2704.0  3015.0   2525.0   2032.0    373.0   
1     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0      0.0   
2     0.0     0.0     0.0     0.0     0.0     0.0      0.0      1.0      0.0   
3     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0      0.0   
4     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0      0.0   

   2/13/20  2/14/20  2/15/20  2/16/20  2/17/20  2/18/20  2/19/20  2/20/20  \
0  15136.0   6463.0   2055.0   2100.0   1921.0   1777.0    408.0    458.0   
1      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2      1.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   2/21/20  2/22/20  2/23/20  2/24/20  2/25/20  2/26/20  2/27/20  2/28/20  \
0    473.0   1451.0     21.0    219.0    513.0    412.0    434.0    328.0   
1      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2      2.0      0.0      0.0     36.0      0.0      6.0      1.0      2.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      2.0      0.0      0.0   

   2/29/20  3/1/20  3/2/20  3/3/20  3/4/20  3/5/20  3/6/20  3/7/20  3/8/20  \
0    428.0   576.0   204.0   125.0   125.0   151.0   153.0    80.0    53.0   
1      0.0     0.0     2.0     0.0    23.0     2.0     1.0     3.0     5.0   
2      8.0     6.0    24.0    20.0    31.0    70.0    48.0   136.0   116.0   
3      0.0     0.0     2.0     0.0     0.0     0.0     2.0     0.0     2.0   
4      2.0     0.0     0.0     1.0     0.0     0.0     1.0     0.0     0.0   

   3/9/20  3/10/20  3/11/20  3/12/20  3/13/20  3/14/20  3/15/20  3/16/20  \
0    37.0     27.0     34.0     11.0     13.0     32.0     26.0     30.0   
1     4.0     13.0      6.0     11.0      9.0     20.0     11.0      6.0   
2    69.0    374.0    323.0    382.0    514.0    548.0    807.0   1125

In [0]:
confirmed_daily.describe() #numerical data

CurrentPopulation          Area       Density  GrowthRate  \
count       1.800000e+02  1.800000e+02    180.000000  180.000000   
mean        4.268585e+07  7.295672e+05    314.812673    1.011952   
std         1.531813e+08  1.978080e+06   1577.076593    0.010822   
min         3.393100e+04  2.020000e+00      2.095900    0.986500   
25%         2.838920e+06  2.949425e+04     32.228875    1.003200   
50%         9.897504e+06  1.451405e+05     86.580950    1.010750   
75%         3.111856e+07  5.588630e+05    201.441325    1.019525   
max         1.439324e+09  1.709824e+07  19426.732700    1.038400   

       WorldPercentage  Cluster Labels         Lat        Long     1/22/20  \
count       180.000000      180.000000  180.000000  180.000000  180.000000   
mean          0.005477        0.100000   19.414931   16.868808    3.083333   
std           0.019652        0.518916   23.616660   58.043258   40.843327   
min           0.000000        0.000000  -40.900600 -102.552800    0.000000   
25%           0.000375        0.000000    5.114075   -9.496275    0.000000   
50%           0.001300        0.000000   17.589246   19.933650    0.000000   
75%           0.004000        0.000000   39.549925   45.009550    0.000000   
max           0.184700        3.000000   64.963100  178.065000  548.000000   

          1/23/20     1/24/20     1/25/20    1/26/20     1/27/20      1/28/20  \
count  180.000000  180.000000  180.000000  180.00000  180.000000   180.000000   
mean     0.550000    1.594444    2.738889    3.80000    4.494444    14.727778   
std      7.081548   20.644557   36.222522   49.85996   59.774950   196.170739   
min      0.000000    0.000000    0.000000    0.00000    0.000000     0.000000   
25%      0.000000    0.000000    0.000000    0.00000    0.000000     0.000000   
50%      0.000000    0.000000    0.000000    0.00000    0.000000     0.000000   
75%      0.000000    0.000000    0.000000    0.00000    0.000000     0.000000   
max     95.000000  277.000000  486.000000  669.00000  802.000000  2632.000000   

          1/29/20      1/30/20      1/31/20       2/1/20       2/2/20  \
count  180.000000   180.000000   180.000000   180.000000   180.000000   
mean     3.266667    11.488889     9.405556    11.727778    26.383333   
std     43.079192   153.090965   123.792929   155.696949   353.220195   
min      0.000000     0.000000     0.000000     0.000000     0.000000   
25%      0.000000     0.000000     0.000000     0.000000     0.000000   
50%      0.000000     0.000000     0.000000     0.000000     0.000000   
75%      0.000000     0.000000     0.000000     0.000000     0.000000   
max    578.000000  2054.000000  1661.000000  2089.000000  4739.000000   

            2/3/20       2/4/20       2/5/20       2/6/20       2/7/20  \
count   180.000000   180.000000   180.000000   180.000000   180.000000   
mean     17.188889    22.283333    20.794444    17.550000    19.644444   
std     230.013742   297.464016   278.237524   234.559072   262.583738   
min       0.000000     0.000000     0.000000     0.000000     0.000000   
25%       0.000000     0.000000     0.000000     0.000000     0.000000   
50%       0.000000     0.000000     0.000000     0.000000     0.000000   
75%       0.000000     0.000000     0.000000     0.000000     0.000000   
max    3086.000000  3991.000000  3733.000000  3147.000000  3523.000000   

            2/8/20       2/9/20      2/10/20      2/11/20     2/12/20  \
count   180.000000   180.000000   180.000000   180.000000  180.000000   
mean     15.161111    16.816667    14.116667    11.333333    2.105556   
std     201.535368   224.720496   188.196595   151.453221   27.800667   
min       0.000000     0.000000     0.000000     0.000000    0.000000   
25%       0.000000     0.000000     0.000000     0.000000    0.000000   
50%       0.000000     0.000000     0.000000     0.000000    0.000000   
75%       0.000000     0.000000     0.000000     0.000000    0.000000   
max    2704.000000  3015.000000  2525.000000  2032.0

> ### C.7.2 **Deaths** Dataframe

In [0]:
deaths_daily = dailyNonCumulative(deaths_data)

In [0]:
deaths_daily.head()

Code        Country  CurrentPopulation       Area   Density  GrowthRate  \
0   CN          China       1.439324e+09  9706961.0  148.2775      1.0039   
1   IN          India       1.380004e+09  3287590.0  419.7617      1.0099   
2   US  United States       3.310027e+08  9372610.0   35.3160      1.0059   
3   ID      Indonesia       2.735236e+08  1904569.0  143.6144      1.0107   
4   PK       Pakistan       2.208923e+08   881912.0  250.4698      1.0200   

   WorldPercentage               Region         Income group  Cluster Labels  \
0           0.1847  East Asia & Pacific  Upper middle income             2.0   
1           0.1770           South Asia  Lower middle income             0.0   
2           0.0425        North America          High income             3.0   
3           0.0351  East Asia & Pacific  Lower middle income             0.0   
4           0.0283           South Asia  Lower middle income             0.0   

         Lat        Long  1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  \
0  32.828385  111.649082     17.0      1.0      8.0     16.0     14.0   
1  21.000000   78.000000      0.0      0.0      0.0      0.0      0.0   
2  37.090200  -95.712900      0.0      0.0      0.0      0.0      0.0   
3  -0.789300  113.921300      0.0      0.0      0.0      0.0      0.0   
4  30.375300   69.345100      0.0      0.0      0.0      0.0      0.0   

   1/27/20  1/28/20  1/29/20  1/30/20  1/31/20  2/1/20  2/2/20  2/3/20  \
0     26.0     49.0      2.0     38.0     42.0    46.0   102.0    64.0   
1      0.0      0.0      0.0      0.0      0.0     0.0     0.0     0.0   
2      0.0      0.0      0.0      0.0      0.0     0.0     0.0     0.0   
3      0.0      0.0      0.0      0.0      0.0     0.0     0.0     0.0   
4      0.0      0.0      0.0      0.0      0.0     0.0     0.0     0.0   

   2/4/20  2/5/20  2/6/20  2/7/20  2/8/20  2/9/20  2/10/20  2/11/20  2/12/20  \
0    66.0    72.0    70.0    85.0    87.0   100.0    107.0    100.0      5.0   
1     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0      0.0   
2     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0      0.0   
3     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0      0.0   
4     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0      0.0   

   2/13/20  2/14/20  2/15/20  2/16/20  2/17/20  2/18/20  2/19/20  2/20/20  \
0    252.0    152.0    142.0    103.0     98.0    139.0    113.0    122.0   
1      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   2/21/20  2/22/20  2/23/20  2/24/20  2/25/20  2/26/20  2/27/20  2/28/20  \
0      0.0    205.0      2.0    150.0     70.0     52.0     29.0     44.0   
1      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   2/29/20  3/1/20  3/2/20  3/3/20  3/4/20  3/5/20  3/6/20  3/7/20  3/8/20  \
0     47.0    35.0    42.0    33.0    36.0    32.0    29.0    28.0    28.0   
1      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
2      1.0     0.0     5.0     1.0     4.0     1.0     2.0     3.0     4.0   
3      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
4      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   

   3/9/20  3/10/20  3/11/20  3/12/20  3/13/20  3/14/20  3/15/20  3/16/20  \
0    23.0     16.0     22.0     11.0      8.0     13.0     10.0     14.0   
1     0.0      0.0      1.0      0.0      1.0      0.0      0.0      0.0   
2     1.0      6.0      8.0      6.0      8.0     10.0     14.0     26

In [0]:
deaths_daily.describe() #numerical data

CurrentPopulation          Area       Density  GrowthRate  \
count       1.800000e+02  1.800000e+02    180.000000  180.000000   
mean        4.268585e+07  7.295672e+05    314.812673    1.011952   
std         1.531813e+08  1.978080e+06   1577.076593    0.010822   
min         3.393100e+04  2.020000e+00      2.095900    0.986500   
25%         2.838920e+06  2.949425e+04     32.228875    1.003200   
50%         9.897504e+06  1.451405e+05     86.580950    1.010750   
75%         3.111856e+07  5.588630e+05    201.441325    1.019525   
max         1.439324e+09  1.709824e+07  19426.732700    1.038400   

       WorldPercentage  Cluster Labels         Lat        Long     1/22/20  \
count       180.000000      180.000000  180.000000  180.000000  180.000000   
mean          0.005477        0.050000   19.414931   16.868808    0.094444   
std           0.019652        0.304069   23.616660   58.043258    1.267105   
min           0.000000        0.000000  -40.900600 -102.552800    0.000000   
25%           0.000375        0.000000    5.114075   -9.496275    0.000000   
50%           0.001300        0.000000   17.589246   19.933650    0.000000   
75%           0.004000        0.000000   39.549925   45.009550    0.000000   
max           0.184700        3.000000   64.963100  178.065000   17.000000   

          1/23/20     1/24/20     1/25/20     1/26/20     1/27/20     1/28/20  \
count  180.000000  180.000000  180.000000  180.000000  180.000000  180.000000   
mean     0.005556    0.044444    0.088889    0.077778    0.144444    0.272222   
std      0.074536    0.596285    1.192570    1.043498    1.937926    3.652244   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
50%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
75%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
max      1.000000    8.000000   16.000000   14.000000   26.000000   49.000000   

          1/29/20     1/30/20     1/31/20      2/1/20      2/2/20      2/3/20  \
count  180.000000  180.000000  180.000000  180.000000  180.000000  180.000000   
mean     0.011111    0.211111    0.233333    0.255556    0.572222    0.355556   
std      0.149071    2.832353    3.130495    3.428638    7.602580    4.770278   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
50%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
75%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
max      2.000000   38.000000   42.000000   46.000000  102.000000   64.000000   

           2/4/20      2/5/20      2/6/20      2/7/20      2/8/20      2/9/20  \
count  180.000000  180.000000  180.000000  180.000000  180.000000  180.000000   
mean     0.366667    0.400000    0.388889    0.472222    0.483333    0.555556   
std      4.919350    5.366563    5.217492    6.335526    6.484597    7.453560   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
50%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
75%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
max     66.000000   72.000000   70.000000   85.000000   87.000000  100.000000   

          2/10/20     2/11/20     2/12/20     2/13/20     2/14/20     2/15/20  \
count  180.000000  180.000000  180.000000  180.000000  180.000000  180.000000   
mean     0.594444    0.555556    0.027778    1.405556    0.844444    0.794444   
std      7.975309    7.453560    0.372678   18.782702   11.329411   10.583901   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
50%      0.0000

> ### C.7.3 **Recoveries** Dataframe

In [0]:
recoveries_daily = dailyNonCumulative(recoveries_data)

In [0]:
recoveries_daily.head()

Code        Country  CurrentPopulation       Area   Density  GrowthRate  \
0   CN          China       1.439324e+09  9706961.0  148.2775      1.0039   
1   IN          India       1.380004e+09  3287590.0  419.7617      1.0099   
2   US  United States       3.310027e+08  9372610.0   35.3160      1.0059   
3   ID      Indonesia       2.735236e+08  1904569.0  143.6144      1.0107   
4   PK       Pakistan       2.208923e+08   881912.0  250.4698      1.0200   

   WorldPercentage               Region         Income group  Cluster Labels  \
0           0.1847  East Asia & Pacific  Upper middle income             2.0   
1           0.1770           South Asia  Lower middle income             0.0   
2           0.0425        North America          High income             1.0   
3           0.0351  East Asia & Pacific  Lower middle income             0.0   
4           0.0283           South Asia  Lower middle income             0.0   

         Lat        Long  1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  \
0  32.828385  111.649082     28.0      2.0      6.0      3.0     10.0   
1  21.000000   78.000000      0.0      0.0      0.0      0.0      0.0   
2  37.090200  -95.712900      0.0      0.0      0.0      0.0      0.0   
3  -0.789300  113.921300      0.0      0.0      0.0      0.0      0.0   
4  30.375300   69.345100      0.0      0.0      0.0      0.0      0.0   

   1/27/20  1/28/20  1/29/20  1/30/20  1/31/20  2/1/20  2/2/20  2/3/20  \
0      9.0     43.0     19.0     15.0     79.0    61.0   188.0   151.0   
1      0.0      0.0      0.0      0.0      0.0     0.0     0.0     0.0   
2      0.0      0.0      0.0      0.0      0.0     0.0     0.0     0.0   
3      0.0      0.0      0.0      0.0      0.0     0.0     0.0     0.0   
4      0.0      0.0      0.0      0.0      0.0     0.0     0.0     0.0   

   2/4/20  2/5/20  2/6/20  2/7/20  2/8/20  2/9/20  2/10/20  2/11/20  2/12/20  \
0   229.0   272.0   362.0   522.0   597.0   623.0    699.0    718.0    446.0   
1     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0      0.0   
2     0.0     0.0     0.0     0.0     0.0     3.0      0.0      0.0      0.0   
3     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0      0.0   
4     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0      0.0   

   2/13/20  2/14/20  2/15/20  2/16/20  2/17/20  2/18/20  2/19/20  2/20/20  \
0   1135.0   1760.0   1321.0   1457.0   1707.0   1744.0   1756.0   2052.0   
1      0.0      0.0      0.0      3.0      0.0      0.0      0.0      0.0   
2      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   2/21/20  2/22/20  2/23/20  2/24/20  2/25/20  2/26/20  2/27/20  2/28/20  \
0    690.0   3995.0    488.0   1828.0   2661.0   2408.0   2846.0   3399.0   
1      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2      2.0      0.0      0.0      0.0      1.0      0.0      0.0      1.0   
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   2/29/20  3/1/20  3/2/20  3/3/20  3/4/20  3/5/20  3/6/20  3/7/20  3/8/20  \
0   2991.0  2842.0  2692.0  2596.0  2551.0  2291.0  1652.0  1595.0  1849.0   
1      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
2      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
3      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
4      0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0     1.0   

   3/9/20  3/10/20  3/11/20  3/12/20  3/13/20  3/14/20  3/15/20  3/16/20  \
0  1416.0   1377.0   1463.0   1257.0   1295.0   1464.0   1357.0    893.0   
1     0.0      1.0      0.0      0.0      0.0      0.0      9.0      0.0   
2     0.0      1.0      0.0      4.0      0.0      0.0      0.0      5

In [0]:
recoveries_daily.describe() #numerical data

CurrentPopulation          Area       Density  GrowthRate  \
count       1.800000e+02  1.800000e+02    180.000000  180.000000   
mean        4.268585e+07  7.295672e+05    314.812673    1.011952   
std         1.531813e+08  1.978080e+06   1577.076593    0.010822   
min         3.393100e+04  2.020000e+00      2.095900    0.986500   
25%         2.838920e+06  2.949425e+04     32.228875    1.003200   
50%         9.897504e+06  1.451405e+05     86.580950    1.010750   
75%         3.111856e+07  5.588630e+05    201.441325    1.019525   
max         1.439324e+09  1.709824e+07  19426.732700    1.038400   

       WorldPercentage  Cluster Labels         Lat        Long     1/22/20  \
count       180.000000      180.000000  180.000000  180.000000  180.000000   
mean          0.005477        0.038889   19.460195   16.769115    0.155556   
std           0.019652        0.220813   23.679444   58.240153    2.086997   
min           0.000000        0.000000  -40.900600 -106.346800    0.000000   
25%           0.000375        0.000000    5.114075   -9.496275    0.000000   
50%           0.001300        0.000000   17.589246   19.933650    0.000000   
75%           0.004000        0.000000   39.549925   45.009550    0.000000   
max           0.184700        2.000000   64.963100  178.065000   28.000000   

          1/23/20     1/24/20     1/25/20     1/26/20    1/27/20     1/28/20  \
count  180.000000  180.000000  180.000000  180.000000  180.00000  180.000000   
mean     0.011111    0.033333    0.016667    0.072222    0.05000    0.255556   
std      0.149071    0.447214    0.223607    0.762461    0.67082    3.211575   
min      0.000000    0.000000    0.000000    0.000000    0.00000    0.000000   
25%      0.000000    0.000000    0.000000    0.000000    0.00000    0.000000   
50%      0.000000    0.000000    0.000000    0.000000    0.00000    0.000000   
75%      0.000000    0.000000    0.000000    0.000000    0.00000    0.000000   
max      2.000000    6.000000    3.000000   10.000000    9.00000   43.000000   

          1/29/20     1/30/20     1/31/20      2/1/20      2/2/20      2/3/20  \
count  180.000000  180.000000  180.000000  180.000000  180.000000  180.000000   
mean     0.105556    0.094444    0.438889    0.344444    1.044444    0.838889   
std      1.416176    1.127102    5.888312    4.546866   14.012693   11.254875   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
50%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
75%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
max     19.000000   15.000000   79.000000   61.000000  188.000000  151.000000   

           2/4/20      2/5/20      2/6/20      2/7/20      2/8/20      2/9/20  \
count  180.000000  180.000000  180.000000  180.000000  180.000000  180.000000   
mean     1.272222    1.511111    2.016667    2.911111    3.361111    3.488889   
std     17.068652   20.273683   26.981573   38.906892   44.496282   46.434370   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
50%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
75%      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
max    229.000000  272.000000  362.000000  522.000000  597.000000  623.000000   

          2/10/20     2/11/20     2/12/20      2/13/20      2/14/20  \
count  180.000000  180.000000  180.000000   180.000000   180.000000   
mean     3.900000    4.094444    2.594444     6.361111     9.794444   
std     52.099615   53.513920   33.239557    84.595110   131.181511   
min      0.000000    0.000000    0.000000     0.000000     0.000000   
25%      0.000000    0.000000    0.000000     0.000000     0.000000   
50%      0.000000    0.000000    0.000000     0.000000     0.000000   
75%      0.00

# D. **Results and Discussion**
---

> In possession of the pre-processed and cleaned datasets, in this section, visualizations were plotted and patterns were pointed out regarding the accumulated evolution of cases, non-cumulative evolution of cases and the current accumulated values of cases, from four different stand points: Clusters, Countries' grouped by their regions, Countries' grouped by their income groups and countries by themselves.

### **D.1** Exploring the daily **Accumulated Evolution of Cases**



> ###### Defining a function to show the world map with the countries colored by their belonging clusters

In [0]:
def ShowClustersMap(df, category, colorscale):

  #getting ISO Alpha-3 codes from ISO Alpha-2
  temp_df = df.copy() 
  values_list = []
  iso_codes_df = pd.read_csv('https://gist.githubusercontent.com/radcliff/f09c0f88344a7fcef373/raw/2753c482ad091c54b1822288ad2e4811c021d8ec/wikipedia-iso-country-codes.csv')

  for index_i, value_i in enumerate(temp_df['Code'].tolist()):
    for value_j in iso_codes_df['Alpha-2 code'].tolist():

      if value_i == value_j :
        values_list.append(list(iso_codes_df[iso_codes_df['Alpha-2 code'] == value_i]['Alpha-3 code'].values))

    if index_i != len(values_list)-1:
      values_list.append(np.nan)

  #inserting ISO Alpha-3 codes in the 0th column of temp_df and standardizing
  temp_df.insert(0, 'IsoAlpha3', values_list)
  temp_df.dropna(inplace=True)
  temp_df.reset_index(inplace=True, drop=True)
  temp_df['IsoAlpha3'] = temp_df['IsoAlpha3'].apply(lambda x: (str(x).split('[')[1].split(']')[0])[1:-1])

  #additonal importing
  import plotly.graph_objects as go

  from IPython.display import Javascript
  display(Javascript('''google.colab.output.setIframeHeight(0, true, {maxHeight: 5000})'''))

  #plotting clustered countries
  fig = go.Figure(data=go.Choropleth(
      locations = temp_df['IsoAlpha3'],
      z = temp_df['Cluster Labels'],
      text = temp_df['Country'],
      colorscale = str(colorscale),
      autocolorscale=False,
      reversescale=False,
      marker_line_color='white',
      marker_line_width=0.5,
      colorbar_tickprefix = '',
      colorbar_title = 'Cluster Labels',
    ))

  fig.update_layout(
      title_text= f"Countries Clustered by {str(category)}' time series | (hover over the map to visualize specifics)",
      geo=dict(
          showframe=False,
          showcoastlines=False,
          projection_type='equirectangular'
      ),
      annotations = [dict(
          x=0.55,
          y=0.1,
          xref='paper',
          yref='paper',
          text='',
          showarrow = False
    )], 
    width=1200,
    height=600
  )

  fig.show()

> ###### Defining a function to plot three differente Area Plots and show the data by the stand points of: Clusters, Income Groups and Regions

In [0]:
def EvolutionAreaPlot(df, category):
  
  #pre-processing
  plot_df = pd.concat([df.iloc[:, 0:2], df.iloc[:, 7:]], axis=1)
  
  #unpivoting
  df_plot = plot_df.melt(id_vars=['Code', 'Country', 'Region', 'Income group', 'Cluster Labels', 'Lat', 'Long'],
                                var_name='Date',
                                value_name=str(category))
  df_plot['Cluster Labels'] = df_plot['Cluster Labels'].apply(lambda x: int(x))

  #additional exporting to avoid bugs
  import plotly.express as px 

  from IPython.display import Javascript
  display(Javascript('''google.colab.output.setIframeHeight(0, true, {maxHeight: 5000})'''))

  #area plot by clusters
  fig = px.area(df_plot, x="Date",
              y=str(category),
              color='Cluster Labels',
              line_group='Country',
              width = 1300,
              title='Clusters Stand Point Visualization | (hover over the plot to visualize Countries data points)'
              )
  fig.update_layout(
    xaxis=dict(showgrid=True, zeroline=False),
    yaxis=dict(showgrid=True, zeroline=False),
  )

  fig.update_xaxes(tick0=0, dtick=14)
  fig.update_yaxes(tick0=np.power(10,6))
  fig.show() 

  #area plot by income group
  fig = px.area(df_plot, x="Date",
              y=str(category),
              color='Income group',
              line_group='Country',
              width = 1300,
              title='Income Group Stand Point Visualization | (hover over the plot to visualize Countries data points)'
              )
  fig.update_layout(
    xaxis=dict(showgrid=True, zeroline=False),
    yaxis=dict(showgrid=True, zeroline=False)
    
  )


  fig.update_xaxes(tick0=0, dtick=14)
  fig.show() 

  #area plot by region
  fig = px.area(df_plot, x="Date",
              y=str(category),
              color='Region',
              line_group='Country',
              width = 1300,
              title='Region Stand Point Visualization | (hover over the plot to visualize Countries data points)'
              )
  fig.update_layout(
    xaxis=dict(showgrid=True, zeroline=False),
    yaxis=dict(showgrid=True, zeroline=False),
  )

  fig.update_xaxes(tick0=0, dtick=14)
  fig.show()

  #return df_plot

In [0]:
colors = ['teal', 'redor', 'tealgrn']

> ### D.1.1 **Confirmed Cases**: visualizing the Clustered Countries through a Choropleth Map plot and evolutions of their time series through Area Plots

In [0]:
ShowClustersMap(confirmed_data, 'Confirmed Cases', colors[0])

<IPython.core.display.Javascript object>

> ### From the plot above, we can identify the following:

> #### **Clusters**
>  ##### **Cluster 0**: composed by countries such as the Netherlands, Ecuador, Japan, Mexico and Russia, accounts for approximately 2.5 million confirmed accumulated cases;
>  ##### **Cluster 1**: composed by countries such as Iran, Italy, France and Spain, it is responsible for roughly 20% of the world's accumulated confirmed cases;
>  ##### **Cluster 2**: composed only by China and it corresponds to around 85 thousand accumulated confirmed cases;
>  ##### **Cluster 3**: composed only the United States, it holds accountability for roughly 1.6 million accumulated confirmed cases;


In [0]:
EvolutionAreaPlot(confirmed_data, 'Confirmed Cases')

<IPython.core.display.Javascript object>

> ### From the plots above, we can identify the following:

> #### **Income Groups**
>  ##### **High Income**: composed by countries such as Canada, Spain and France, it is responsible for the great majority of accumulated confirmed cases, adding up to almost 3 million cases;
>  ##### **Upper Middle Income**: with countries like Brazil, Russia, Mexico and Turkey, together accounts for roughly 20% of the confirmed accumulated cases;
>  ##### **Lower Middle Income**: containing countries like India, Indonesia and Pakistan, they add up to almost 250 thousand accumulated cases;
>  ##### **Low Income**: composed by countries such as Liberia, Togo and Gambia, the group hold responsibility for almost 3000 confirmed cases. This number should be interpreted carefully, since a number of those countries do not have the means to perform suitable tests for COVID-19 and it might be drastically higher than stated;

> #### **Regions**
>  ##### **East Asia and Pacific**: currently holds close to 5% of accumulated confirmed cases;
>  ##### **South Asia**: also holds close to 5% of accumulated confirmed cases
>  ##### **North America**: with the 2nd largest number of confirmed accumulated cases, it accounts for almost 35% of the referred metric;
>  ##### **Latin America & Caribean**: holding the 3rd largset amount, it accounts for roughly 600 thousand accumulated cases;
>  ##### **Sub-Saharan Africa**: adding up to less than 2% of the total amount, it the least significant part in terms of quantity of accumulated confirmed cases. However, this amount should be taken cautiously, taking into consideration accessibility issues that the populations might have to adequate COVID-19 testing;
>  ##### **Europe & Central Asia**: adding up to close to 2 million confirmed accumulated cases, it holds the 1st place in quantity terms;
>  ##### **Middle East & North Africa**: responsible for less than 10% of worlwide accumulated confirmed cases. This amount should also be interpreted with care, as it might be over or understated, due to possible issues in properly testing for the disease;

> ### D.1.2 **Deaths**: visualizing the Clustered Countries and evolutions of their time series through Area Plots

In [0]:
ShowClustersMap(deaths_data, 'Deaths', colors[1])

<IPython.core.display.Javascript object>

> ### From the plot above, currently, it is feasible to identify the following:

> #### **Clusters**
>  ##### **Cluster 0**: composed by countries such as the Denmark, Ecuador and Poland, accounts for approximately 100 thousand accumulated deaths;
>  ##### **Cluster 1**: composed only by China, it holds accountability for almost 5 thousand accumulated deaths;
>  ##### **Cluster 2**: composed by countries such as United Kingdom, France and Italy, it is responsible for roughly 125 thousand accumulated deaths;
>  ##### **Cluster 3**: composed only by the United States, it alone, accounts for roughly 100 thousand deaths;


In [0]:
EvolutionAreaPlot(deaths_data, 'Deaths')

<IPython.core.display.Javascript object>

> ### From the plots above, currently, it is feasible to identify the following:

> #### **Income Groups**
>  ##### **High Income**: composed by countries such as Canada, Spain and France, it is responsible for the great majority of accumulated deaths, coming up to roughly 250 thousand;
>  ##### **Upper Middle Income**: with countries like Brazil, Russia, Mexico and Turkey, together accounts for almost 50 thousand accumulated deaths;
>  ##### **Lower Middle Income**: containing countries like India, Indonesia and Pakistan, they add up to almost 10 thousand accumulated deaths;
>  ##### **Low Income**: composed by countries such as Liberia, Togo and Gambia, the group hold responsibility for less than 1 thousand accumulated deaths;

> #### **Regions**
>  ##### **East Asia and Pacific**: holds close to 2.5% of accumulated deaths;
>  ##### **South Asia**: holds close to 1.5% of accumulated deaths;
>  ##### **North America**: with the 2nd largest number of deaths cases, it accounts for almost 35%;
>  ##### **Latin America & Caribbean**: holding the 3rd largset amount, it accounts for roughly 10% accumulated deaths;
>  ##### **Sub-Saharan Africa**: adding up to less than 1% of the total amount, it the least significant part in terms of quantity of accumulated deaths;
>  ##### **Europe & Central Asia**: adding up to roughly 170 thousand  acummulated deaths, it hold the 1st place in quantity terms;
>  ##### **Middle East & North Africa**: responsible for close to 3% of wordlwide accumulated deaths;

> ### D.1.3 **Recoveries**: visualizing the Clustered Countries and evolutions of their time series through Area Plots

In [0]:
ShowClustersMap(recoveries_data, 'Recoveries', colors[2])

<IPython.core.display.Javascript object>

> ### From the plots above, currently, it is possible to identify the following:

> #### **Clusters**
>  ##### **Cluster 0**: composed by countries such as the Ireland, Sweden and Canada, accounts for approximately 1 million accumulated recoveries;
>  ##### **Cluster 1**: composed by countries such as United States, Germany, France and Italy, it is responsible for roughly 900 thousand accumulated recoveries;
>  ##### **Cluster 2**: composed only by China, it holds accountability for almost 80 thousand accumulated recoveries;


In [0]:
EvolutionAreaPlot(recoveries_data, 'Recoveries')

<IPython.core.display.Javascript object>

> ### From the plots above, currently, it is possible to identify the following:

> #### **Income Groups**
>  ##### **High Income**: composed by countries such as Canada, Spain and France, it is responsible for the great majority of accumulated recoveries, adding up to a little higher than 1.2 million;
>  ##### **Upper Middle Income**: with countries like Brazil, Russia, Mexico and Turkey, together accounts for loosely 700 thousand accumulated recoveries;
>  ##### **Lower Middle Income**: containing countries like India, Indonesia and Pakistan, they add up to almost 120 thousand accumulated recoveries
>  ##### **Low Income**: composed by countries such as Liberia, Togo and Gambia, the group hold responsibility for less than 1% thousand accumulated recoveries. Nonetheless, since its confirmed accumulated cases numbers might not be very reliable, the accumulated number of recoveries may as well be affected by it;

> #### **Regions**
>  ##### **East Asia and Pacific**: currently holds close to 7% of accumulated recoveries;
>  ##### **South Asia**: holds close to 3.5% of accumulated recoveries;
>  ##### **North America**: with the 2nd largest number of recoveries, it accounts for almost 20% of the wordlwide total;
>  ##### **Latin America & Caribbean**: holding the 3rd largest amount, it accounts for roughly 13% accumulated recoveries;
>  ##### **Sub-Saharan Africa**: adding up to less than 2% of the total amount, it the least significant part in terms of quantity of accumulated recveries. Yet, this number should be taken with a grain of salt, since the equivalent accumulated confirmed cases are not totally reliable and might affect it as well;
>  ##### **Europe & Central Asia**: adding up to roughly 950 thousand  accumulated recoveries, it holds the 1st place in quantity terms;
>  ##### **Middle East & North Africa**: responsible for close to 10% of worldwide accumulated recoveries;

### **D.2** Exploring the **Current** Accumulated values of Confirmed cases, Deaths and Recoveries


> ###### Defining a function to plot visualizations of Current Acummulated Cases Worldwide with:


*   Scattergeo
*   Funnel Plots



In [0]:
def AcummulatedWorldwide():

  '''Pre-processing'''

  temp_ll = current_data.copy()
  sizes_list = [3, 6, 9, 18, 27, 54]

  #binning Confirmed, Deaths and Recoveries into 6 bins
  for col in temp_ll.columns[-6:-3]:

    temp_ll[str(col)+'Binned'] = pd.qcut(temp_ll[col], q=6, labels=sizes_list)
    temp_ll[str(col)+'Binned'] = pd.to_numeric(temp_ll[str(col)+'Binned'])

  from IPython.display import Javascript
  display(Javascript('''google.colab.output.setIframeHeight(0, true, {maxHeight: 5000})'''))

  '''Scattergeo Plot'''
  from plotly import graph_objects as go
  fig = go.Figure()
  #confirmed
  fig.add_trace(go.Scattergeo(
          lon = temp_ll['Long'],
          lat = temp_ll['Lat'],
          text = temp_ll['Confirmed'],
          mode="markers",
          name = 'Confirmed',
          marker = dict(
                size =  temp_ll['ConfirmedBinned']+15,
                color = 'royalblue',
                line_width = 0,
                opacity=0.4
                
            )))
  #deaths
  fig.add_trace(go.Scattergeo(
          lon = temp_ll['Long'],
          lat = temp_ll['Lat'],
          text = temp_ll['Deaths'],
          name = 'Deaths',
          marker = dict(
                size = temp_ll['DeathsBinned'],
                color = 'salmon',
                line_width =0,
                opacity=0.4,
            )))
  #recoveries
  fig.add_trace(go.Scattergeo(
          lon = temp_ll['Long'],
          lat = temp_ll['Lat'],
          text = temp_ll['Recoveries'],
          name = 'Recoveries',
          marker = dict(
                size = temp_ll['RecoveriesBinned'],
                color = 'lightgreen',
                line_width = 0,
                opacity=0.6,
                sizemode='area'
            )))
  #countries' names
  fig.add_trace(go.Scattergeo(
          lon = temp_ll['Long'],
          lat = temp_ll['Lat'],
          text = temp_ll['Country'],
          name='',
          marker = dict(
                size = 0,
                color = 'gray',
                line_width = 0,
                opacity=0,
            )))

  fig.update_layout(geo = go.layout.Geo(
        resolution = 110,
        scope = 'world',
        showframe = False,
        showcoastlines = False,
        landcolor = "rgb(204, 204, 204)",
        countrycolor = "white" ,
        coastlinecolor = "white",
        projection_type = 'equirectangular',
        domain = dict(x = [ 1, 1 ], y = [ 1, 1 ])
    ),
    height=800,
    width=1300,
    title = 'Current Acummulated Confirmed Cases, Deaths and Recoveries Worldwide | (zoom in to visualize specifics)')

  fig.update_geos(
      visible=True,
      showocean=True,
      oceancolor="azure",
      showcountries=True,
      countrycolor="white"
    )
  fig.show()

  '''Funnel Plots'''
  for criterium in ['Region', 'Income group']:

    funnel_df = current_data.groupby([criterium])[['Confirmed', 'Deaths', 'Recoveries']].sum()
    funnel_df.reset_index(inplace=True)
    funnel_df.sort_values(by='Recoveries', ascending=False, inplace=True)
    
  
    fig = go.Figure(data=[go.Funnel(name= funnel_df.columns[i],
                              y = funnel_df[criterium],
                              x = funnel_df.iloc[:, i],
                              textposition='inside',
                              textinfo = "value+percent total"
                              )
                              for i in range(1, len(funnel_df.columns))])

    fig.update_layout(
      width = 1300,
      height = 500,
      title = f'Total Cases by {criterium} | (hover over the plot to visulize specifics)'
    )

    fig.show()


> ### D.2.1 Accumulated Cases from a **worldwide**, **region** and **income group** stand point

In [0]:
AcummulatedWorldwide()

<IPython.core.display.Javascript object>

> #### Given the plotted map and the funnel plots, one can point out that the leading regions for confirmed cases, deaths and recoveries are Europe & Central Asia and North America, accounting for almost 70% of worldwide confirmed cases, 80% of worldwide deaths and 65% of worldwide recoveries. From an Income Group stand point, it is noticeable that, added together, High Income and Upper Middle Income are responsible, in regards to worldwide numbers, for almost 95% of confirmed cases, 97% of deaths and close to 95% of recoveries.

### **D.3** Visualizing  **Top 10 Countries** in regards to Accumulated Confirmed Cases, Accumulated Deaths and Accumulated Recoveries

> ###### Defining a function to show Funnel Plots regarding the top-n Countries, from a perspective of Accumulated Confirmed Cases, Accumulated Deaths and Accumulated Recoveries

In [0]:
def funnelNCountries(df, n):

  from IPython.display import Javascript
  display(Javascript('''google.colab.output.setIframeHeight(0, true, {maxHeight: 5000})'''))

  plotly_colors = ['#636EFA', '#EF553B', '#00CC96']
  temp = df.copy()
  for criterium, plotly_color in zip(temp.columns[-6:-3], plotly_colors):
    from plotly import graph_objects as go
    temp_df = temp.groupby(['Country'])[[criterium]].sum()
    temp_df.reset_index(inplace=True)
    temp_df.sort_values(by=criterium, ascending=False, inplace=True)
    temp_df.reset_index(inplace=True, drop=True)
    temp_df = temp_df.head(n)
  
    fig = go.Figure(go.Funnel(name= temp_df.columns[0],
                              y = temp_df.iloc[:,0],
                              x = temp_df.iloc[:, -1],
                              textposition='inside',
                              textinfo = "value+percent total",
                              #opacity=0.8
                              marker = {'color': plotly_color}
                              ))
    
    if criterium == temp.columns[-6]:
      criterium = criterium+' Cases'

    fig.update_layout(
      width = 1200,
      height = 600,
      title = f'Top {n} Countries by Acumulated {criterium}'
    )



    fig.show()

> ### D.3.1 **Funnel Plots**

In [0]:
funnelNCountries(current_data, 10)

<IPython.core.display.Javascript object>

> #### From the above graphed, it is a striking fact that the United States alone are responsible for almost half of worldwide confirmed cases, when added together with the United Kingdom, roughly half of worldwide deaths and a little shorter of a quarter of worldwide recoveries.

### **D.4** Exploring the distributions of **daily mortality rates** amongst the 10 countries with highest values of accumulated deaths 

> ###### Defining a function to generate 'n' Violin Plots (including Box Plots) corresponding to the **Top-n countries with the highest accumulated values of deaths** (as presented in topic D.3.1). The referred Violin Plots **present the distribution of daily mortality rates [daily deaths/daily confirmed cases]** of those abovementioned countries

In [0]:
def MortalityNViolinPlots(n):
  
  np_c = confirmed_daily.copy()
  np_d = deaths_daily.copy()

  columns = list(np_c.columns[12:])

  #instanciating dataframe
  mortality_df = pd.DataFrame(index=np_c.Country, columns=columns)
  mortality_df.reset_index(inplace=True)
  import plotly.graph_objects as go

  #putting together the dataframe
  for mr in mortality_df.index:
    mortality_df.iloc[mr, 1:] = np_d.iloc[mr, 12:]/np_c.iloc[mr, 12:]

  mortality_df.fillna(0, inplace=True)

  df = mortality_df.melt(id_vars='Country', var_name='Date', value_name='Daily Mortality Rate')

  top_n = list(current_data.sort_values(by='Deaths', ascending=False)['Country'].head(n))

  #looping through the top n countries and plotting
  fig = go.Figure()
  for country in top_n:

    temp = df[df['Country'] == country]
    y = temp['Daily Mortality Rate']

    #boolean array sinalizing outliers for further filtering
    removed_outliers = y.between(y.quantile(.05), y.quantile(.95)) 

    #plotting
    fig.add_trace(go.Violin(x=temp['Country'],
                          y=y[removed_outliers],
                          name=country,
                          box_visible=True,
                          meanline_visible=True
                          ))


  fig.update_layout(width=1300,
                    height=600,
                    title=f"Top {n} Countries' Daily Mortality Rates Distributions | (hover over the plot to visualize specifics)"
                    )
  fig.update_traces(opacity=0.75)
  fig.show()

> ### D.4.1 Countries' daily mortality distributions

In [0]:
MortalityNViolinPlots(10)

> #### Amongst the countries shown above, one can observe that most of those have distributions fairly concentrated around 0,5% mortality rates, with the exceptions of Italy (relatively balanced around 1% and 15% mortality rates) and Iran (reasonably more concentrated around 6% mortality rates);

>#### It is worth to draw attention to how the variable analysed (Mortality Rate) is structured, since it is the quotient between the number of deaths on a given day and the number of confirmed cases on that same day. Taking that into consideration, values smaller than zero (MR < 0) are possible, for example, for days when the number of recoveries transcends the number of deaths. In sum, it measures proportions, not absolute values;

>#### Despite performing a first iteration of outlier removal for all the 10 countries like France, Belgium and the United Kingdom remain with fairly extreme maximum values (~55%, ~37%, ~28%, respectively). However, it was opted not to perform a 2nd iteration of outlier removal, since those value most likely represent days that had very few new confirmed cases along with fairly high values of deaths, and a such situation would be feasible, for example, at the starting period of a very strict lockdown, where people already infected are dying and the number of newly infected cases decreases greatly.



### **D.5** Exploring **Treemaps** visualizations regarding countries' Regions, Income Groups, Mortality Metrics and Recovery Metrics

> ###### Defining a function to produce a dataframe with weighted averages, for subsequent analysis, by taking as input:

*   A lower granularity categorical attribute 'lga' in df (input)
*   A higher granularity categorical attribute 'hga' also in df (input)
*   The 'variable' to which you desire to calculate the weighted average for
*   The 'weight' to compose the weighted average

In [0]:
def df_WeightedAvg(df, lga, hga, variable, weight):

  try:  
    temp = df.copy()
    lga_list = []
    hga_list = []
    w_avg = []

    for l in temp[str(lga)].unique():
      for h in temp[str(hga)].unique():
        lga_list.append(l)
        hga_list.append(h)
        w_avg.append(((df.loc[(df[str(lga)] == l) & (df[str(hga)] == h), str(variable)])\
                    *(df.loc[(df[str(lga)] == l) & (df[str(hga)] == h), str(weight)])).sum()\
                    /(df.loc[(df[str(lga)] == l) & (df[str(hga)] == h), str(weight)].sum()))

    df_ = pd.DataFrame(list(zip(lga_list, hga_list, w_avg)), columns=[str(lga), str(hga), 'Weighted Avg'])
    df_.dropna(inplace=True)
    df_.reset_index(inplace=True, drop=True)

    return df_

  except:
    
    return None                  

> ### D.5.1 Visualizing **Region** in regards to **Income group**, quantified by the **value of accumulated cases**

In [0]:
data_dict = {'Confirmed Cases': confirmed_data,
             'Deaths': deaths_data,
             'Recoveries': recoveries_data}

from IPython.display import Javascript
display(Javascript('''google.colab.output.setIframeHeight(0, true, {maxHeight: 5000})'''))

for item, value, color in zip(list(data_dict), list(data_dict.values()), colors):

  temp = value.groupby(['Income group', 'Region', 'Country'])[value.columns[-1]].max().reset_index()
  temp.rename({temp.columns[-1]:'Cases'}, axis=1, inplace=True)
  fig = px.treemap(temp, path=['Income group','Region'], values= temp.columns[-1],
                  color = temp.columns[-1], hover_data=['Region'],
                  color_continuous_scale=color,
                  title=item,
                  width = 1200,
                  height = 600,
                 )
  fig.show()

<IPython.core.display.Javascript object>

> #### Given the treemaps above, one can infer that, from a worldwide perspective, higher income regions currently hold the majority of confirmed cases, a vast amount of deaths, and a proportionally large number of recoveries.

> #### The lower middle and low income regions added together represent close to one third of confirmed cases, 18% of deaths and a disproportionately lower percentage of recoveries (a little higher than 5% worldwide recoveries)

> ### D.5.2 Visualizing **Countries** in regards to **Region**, quantified by the **value of accumulated cases**

In [0]:
import plotly.express as px

from IPython.display import Javascript
display(Javascript('''google.colab.output.setIframeHeight(0, true, {maxHeight: 5000})'''))

for item, value, color in zip(list(data_dict), list(data_dict.values()), colors):

  temp = value.groupby(['Income group', 'Region', 'Country'])[value.columns[-1]].max().reset_index()
  temp.rename({temp.columns[-1]:'Cases'}, axis=1, inplace=True)
  fig = px.treemap(temp, path=['Region', 'Country'], values= temp.columns[-1],
                  color= temp.columns[-1], hover_data=['Income group'],
                  color_continuous_scale= color, 
                  title=item,
                  width = 1200,
                  height = 600,
                 )
  fig.show()

<IPython.core.display.Javascript object>

> #### Given the graphically displayed above, it is discernible an almost even balance between the regions of North America and Europe & Central Asia in terms of confirmed cases;

> #### In terms of deaths, it is evident that Europe & Central Asia alone are responsible for roughly 50% of the worlwide amount and a proportional amount of recoveries (close to 50% as well);

> ### D.5.3 **Mortality** Metrics
 

*   **Region** in regards to **Income group**, quantified by **Mortality Rate** weighted average (weights: **Demographic Density**) [the higher, the worse]
*   **Country** in regards to **Region**, quantified by **Mortality Rate** [deaths/confirmed case]



In [0]:
temp_ir = df_WeightedAvg(current_data, 'Income group', 'Region', 'MortalityRate', 'Density')

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:13: RuntimeWarning:

invalid value encountered in double_scalars



In [0]:
from IPython.display import Javascript
display(Javascript('''google.colab.output.setIframeHeight(0, true, {maxHeight: 5000})'''))

fig = px.treemap(temp_ir, path=['Income group', 'Region'], values= temp_ir.columns[-1],
                  color= temp_ir.columns[-1], hover_data=['Income group'],
                  color_continuous_scale=colors[1], 
                  title='Weighted Averages of Mortality Rates by Demographic Density',
                  width = 1200,
                  height = 600,
                 )
fig.show()

fig = px.treemap(current_data, path=['Income group', 'Region', 'Country'], values= current_data.columns[-2],
                  color= current_data.columns[-2], hover_data=['Region'],
                  color_continuous_scale=colors[1], 
                  title="Countries' Mortality Rates",
                  width = 1200,
                  height = 600,
                 )
fig.show()

<IPython.core.display.Javascript object>

> #### From the plotted above, it is recognizable that, when weighting the countries's mortality rates with their demographic density, the four income groups show fairly close share of deaths amongst each other (roughly a quarter each);

> #### On a non weighted mortality rates perspective, it is prominent that, when added together, the countries with high income stand out, followed by the upper middle income ones, and the low and lower middle income are almost evenly balanced amongst each other;

> ### D.5.4 **Recovery** Metrics

*   **Region** in regards to **Income group**, quantified by **Recovery Rate** weighted average (weights: **Demographic Density**) [the higher, the better]
*   **Country** in regards to **Region**, quantified by **Recovery Rate** [recoveries/confirmed case]

In [0]:
temp_rr = df_WeightedAvg(current_data, 'Income group', 'Region', 'RecoveryRate', 'Density')

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:13: RuntimeWarning:

invalid value encountered in double_scalars



In [0]:
from IPython.display import Javascript
display(Javascript('''google.colab.output.setIframeHeight(0, true, {maxHeight: 5000})'''))

fig = px.treemap(temp_rr, path=['Income group', 'Region'], values= temp_rr.columns[-1],
                  color= temp_rr.columns[-1], hover_data=['Income group'],
                  color_continuous_scale=colors[2], 
                  title='Weighted Averages of Recovery Rates by Demographic Density',
                  width = 1200,
                  height = 600,
                 )
fig.show()


fig = px.treemap(current_data, path=['Income group', 'Region', 'Country'], values= current_data.columns[-1],
                  color= current_data.columns[-1], hover_data=['Income group'],
                  color_continuous_scale=colors[2], 
                  title="Countries' Recovery Rates",
                  width = 1200,
                  height = 600,
                 )
fig.show()


<IPython.core.display.Javascript object>

> #### On the basis of the shown in the above treemaps, one can presume that, when weighting the countries's recovery rates with its demographic density, the high and upper middle income ones show a fairly equal share amongst each other. When grouping together the low and lower middle income countries, the low income ones present a share of roughly one third of the referred sub-group;

> #### When taking a glimpse at the non weighted countries' recovery rates, it is evident that Europe & Central Asia stand out amongst the high income countries, Latin America & Caribbean takes the bigger share on the upper middle income group. On the lower middle income East Asia & Pacific and Sub-Saharan Africa hold almost even shares amongst each other. Regarding the low income countries, the ones belonging to Sub-Saharan Africa take up the vast majority regarding the referred metric;

# E. **Conclusion and Final Discussions**
---

> Motivated by the problem at hand (COVID-19's Pandemic), data was gathered, preprocessed, clustered, grouped by income groups, regions and incidences of an array of criteria. Visualizations trough maps, area plots, violin plots, box plots, funnel plots and treemaps were charted, so that patterns and underlying characteristics could be highlighted on the data, in an effort to produce meaningful insights on how the phenomenon carries itself out across time (evolution of cases) and in terms of current accumulated cases. 

> On the basis of what was shown and vastly addressed in this study, it is possible to state that high income countries have the highest values on all three metrics (confirmed cases, deaths and recoveries), all fairly proportional amongst each other. Nevertheless, it is quite possible that those countries' populations have vastly larger access to proper COVID-19 testing, which presumably overstates the metrics in regards to the rest of the income groups, due to broader resources, mainly financial.

> Supplementary, data collection and reporting for very poor/low income countries (such as Kenya) or countries in conflict regions (such as Syria), for example, might be highly inexact as a consequence of a severe lack of resources to test for the disease and, in many cases, even gathering data might be very challenging or, at times, impossible. Another valid point is the measuring and bounding of the impacts that the asymptomatic positive cases could impose on a vast array of aspects is greatly unknown and could potentially mask the data in very complex and unpredicted ways. 

> 







# F. **Future Directions**
---



> Given the fact that the repository used as data source for this project is daily updaded, it would be advisable to carry on running the codes and functions to visualize possible changes in the shapes and patterns that the data might have and quite possibly change the codes depending on specific changes.

> A more thorough and in-depth study of outliers and how they interact with the health politics and isolation protocols that each individual country is performing would be desirable, as they can potentially bias conclusions and traced patterns, or, at the other end of the spectrum, highly improve the yielded insights and positive results.

# G. **References**

> [1] WHO Timeline - COVID-19. World Health Organization (WHO). Available at: https://www.who.int/news-room/detail/27-04-2020-who-timeline---covid-19

> [2] Coronavirus Overview. World Health Organization (WHO). Available at: https://www.who.int/health-topics/coronavirus#tab=tab_1

> [3] Coronavirus Symptoms. World Health Organization (WHO). Available at: https://www.who.int/health-topics/coronavirus#tab=tab_3

> [4] Novel Coronavirus (COVID-19) Github Repository. Johns Hopkins University Center for Systems Science and Engineering. Available at: https://github.com/CSSEGISandData?tab=repositories

> [5] World Bank Country and Lending Groups. The World Bank. Available at: https://datahelpdesk.worldbank.org/knowledgebase/articles/906519-world-bank-country-and-lending-groups